In [1]:
import pandas as pd
import requests
import xmltodict
import json
import matplotlib.pyplot as plt
from fuzzywuzzy import fuzz
from dataclasses import dataclass, asdict

C:\Users\vigrose\AppData\Local\Continuum\anaconda3\lib\site-packages\fuzzywuzzy\fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


In [2]:
@dataclass
class NumberSearch:
    number: int = ''
    version: str = '2.1'
    enumeration_type: any = 'NPI-2'

In [3]:
@dataclass
class Search:
    organization_name: str = ''
    state: str = ''
    city: str = ''
    postal_code: int = ''
    taxonomy_desc: str = ''
    version: str = '2.1'
    enumeration_type: any = 'NPI-2'

In [4]:
def get_results(search):
    url = 'https://npiregistry.cms.hhs.gov/api/?version=2.1'
    parameters = asdict(search)
    response =  requests.get(url, params=parameters)
    results = response.json()
    return results

In [5]:
def parse_results(results, customer_key):
    dict_list = []
    try:
        count = results['result_count']
    except KeyError:
        return dict_list
    if count > 0:
        for result in results['results']:
            npi = result['number']
            name = result['basic']['organization_name']
            if result['other_names']:
                other_name = result['other_names'][0]['organization_name']
            else:
                other_name = "None"
            date = result['basic']['last_updated']
            taxonomy = result['taxonomies'][0]['desc']
            for address in result['addresses']:
                if address['address_purpose']=='MAILING':
                    mailing_address = address['address_1']
                    mailing_zip = address['postal_code']
                    mailing_state = address['state']
                    mailing_city = address['city']
                if address['address_purpose']=='LOCATION':
                    location_address = address['address_1']
                    location_zip = address['postal_code']
                    location_state = address['state']
                    location_city = address['city']
            subpart = result['basic']['organizational_subpart']
            new_dict = {
                'CUSTOMER_KEY':customer_key,
                'NAME':name,
                'OTHER_NAME': other_name,
                'NPI': npi,
                'TAXONOMY':taxonomy,
                'SUBPART':subpart,
                'MAILING_ADDRESS': mailing_address,
                'MAILING_ZIP': mailing_zip,
                'MAILING_CITY': mailing_city,
                'MAILING_STATE': mailing_state,
                'LOCATION_ADDRESS': location_address,
                'LOCATION_ZIP': location_zip,
                'LOCATION_CITY': location_city,
                'LOCATION_STATE': location_state,
                'UPDATED': date
            }
            dict_list.append(new_dict)
    return dict_list

In [7]:
def get_npi_info(results, customer_number):
    result = results['results'][0]
    name = result['basic']['organization_name']
    npi = result['number']
    if result['other_names']:
        other_name = result['other_names'][0]['organization_name']
    else:
        other_name = "None"
    dict_list =[]
    for address in result['addresses']:
        if address['address_purpose']=='MAILING':
            mailing_address = address['address_1']
            mailing_zip = address['postal_code']
            mailing_state = address['state']
            mailing_city = address['city']
        if address['address_purpose']=='LOCATION':
            location_address = address['address_1']
            location_zip = address['postal_code']
            location_state = address['state']
            location_city = address['city']
    new_dict = {
                'CUSTOMER_NUMBER':customer_number,
                'NAME':name,
                'OTHER_NAME': other_name,
                'NPI': npi,
                'MAILING_ADDRESS': mailing_address,
                'MAILING_ZIP': mailing_zip,
                'MAILING_CITY': mailing_city,
                'MAILING_STATE': mailing_state,
                'LOCATION_ADDRESS': location_address,
                'LOCATION_ZIP': location_zip,
                'LOCATION_CITY': location_city,
                'LOCATION_STATE': location_state,
            }
    dict_list.append(new_dict)
    return dict_list

In [8]:
x = NumberSearch(1720182835)
get_npi_info(get_results(x), 55)

[{'CUSTOMER_NUMBER': 55,
  'NAME': 'LIMESTONE MEDICAL CENTER, INC',
  'OTHER_NAME': 'LIMESTONE AMBULATORY SURGERY CENTER',
  'NPI': 1720182835,
  'MAILING_ADDRESS': 'PO BOX 5030',
  'MAILING_ZIP': '198080030',
  'MAILING_CITY': 'WILMINGTON',
  'MAILING_STATE': 'DE',
  'LOCATION_ADDRESS': '1941 LIMESTONE RD STE 113',
  'LOCATION_ZIP': '198085413',
  'LOCATION_CITY': 'WILMINGTON',
  'LOCATION_STATE': 'DE'}]

In [176]:
import datamart

In [180]:
customers = datamart.get_datamart_results((6),(2020))

In [186]:
customer_list = customers.drop_duplicates('CUSTOMER_NAME')

In [210]:
dict_list =[]
for row in customer_list.itertuples():
    cus_name = row.CUSTOMER_NAME.replace('+','')+'*'
    new_results = get_results(Search(cus_name))
    parsed = parse_results(new_results, row.CUSTOMER_KEY)
    print(parsed)
    if parsed:
        dict_list+=parsed   
    else:
        print(f'No results found')         
    print('---')

[{'CUSTOMER_KEY': '60362', 'NAME': 'SWEENY HOSPITAL DISTRICT', 'NPI': 1023011657, 'TAXONOMY': 'Emergency Medicine', 'CATEGORY': 'Hospital', 'SUBPART': 'NO', 'MAILING_ADDRESS': '305 N MCKINNEY ST', 'MAILING_ZIP': '774802801', 'MAILING_CITY': 'SWEENY', 'MAILING_STATE': 'TX', 'LOCATION_ADDRESS': '305 N MCKINNEY ST', 'LOCATION_ZIP': '774802801', 'LOCATION_CITY': 'SWEENY', 'LOCATION_STATE': 'TX', 'UPDATED': '2019-08-23'}]
---
[{'CUSTOMER_KEY': '59896', 'NAME': 'CAMERON MEMORIAL COMMUNITY HOSPITAL INC', 'NPI': 1730357245, 'TAXONOMY': 'Clinic/Center Rural Health', 'CATEGORY': 'Hospital', 'SUBPART': 'NO', 'MAILING_ADDRESS': '1500 W MAUMEE ST', 'MAILING_ZIP': '467038605', 'MAILING_CITY': 'ANGOLA', 'MAILING_STATE': 'IN', 'LOCATION_ADDRESS': '1500 W MAUMEE ST', 'LOCATION_ZIP': '467038605', 'LOCATION_CITY': 'ANGOLA', 'LOCATION_STATE': 'IN', 'UPDATED': '2017-04-11'}, {'CUSTOMER_KEY': '59896', 'NAME': 'CAMERON MEMORIAL COMMUNITY HOSPITAL INC', 'NPI': 1326531179, 'TAXONOMY': 'Clinic/Center Rural Heal

[]
No results found
---
[{'CUSTOMER_KEY': '59598', 'NAME': 'HUNTSVILLE MEMORIAL HOSPITAL', 'NPI': 1417157637, 'TAXONOMY': 'Clinic/Center Adult Mental Health', 'CATEGORY': 'Hospital', 'SUBPART': 'NO', 'MAILING_ADDRESS': 'PO BOX 4001', 'MAILING_ZIP': '773424001', 'MAILING_CITY': 'HUNTSVILLE', 'MAILING_STATE': 'TX', 'LOCATION_ADDRESS': '110 MEMORIAL HOSPITAL DR', 'LOCATION_ZIP': '773404940', 'LOCATION_CITY': 'HUNTSVILLE', 'LOCATION_STATE': 'TX', 'UPDATED': '2007-08-09'}, {'CUSTOMER_KEY': '59598', 'NAME': 'WALKER COUNTY HOSPITAL CORPORATION', 'NPI': 1144225699, 'TAXONOMY': 'General Acute Care Hospital', 'CATEGORY': 'Hospital', 'SUBPART': 'NO', 'MAILING_ADDRESS': '110 MEMORIAL HOSPITAL DR', 'MAILING_ZIP': '773404940', 'MAILING_CITY': 'HUNTSVILLE', 'MAILING_STATE': 'TX', 'LOCATION_ADDRESS': '110 MEMORIAL HOSPITAL DR', 'LOCATION_ZIP': '773404940', 'LOCATION_CITY': 'HUNTSVILLE', 'LOCATION_STATE': 'TX', 'UPDATED': '2008-04-20'}, {'CUSTOMER_KEY': '59598', 'NAME': 'WALKER COUNTY HOSPITAL CORPORAT

[{'CUSTOMER_KEY': '71238', 'NAME': "CHILDREN'S HOSPITAL OF WISCONSIN", 'NPI': 1689787541, 'TAXONOMY': 'Audiologist', 'CATEGORY': 'Hospital', 'SUBPART': 'NO', 'MAILING_ADDRESS': 'W147N10748 HERITAGE PKWY', 'MAILING_ZIP': '530224389', 'MAILING_CITY': 'GERMANTOWN', 'MAILING_STATE': 'WI', 'LOCATION_ADDRESS': 'W147N10748 HERITAGE PKWY', 'LOCATION_ZIP': '530224389', 'LOCATION_CITY': 'GERMANTOWN', 'LOCATION_STATE': 'WI', 'UPDATED': '2007-07-08'}, {'CUSTOMER_KEY': '71238', 'NAME': "CHILDREN'S HOSPITAL OF WISCONSIN", 'NPI': 1992810667, 'TAXONOMY': 'General Acute Care Hospital Children', 'CATEGORY': 'Hospital', 'SUBPART': 'NO', 'MAILING_ADDRESS': '9000 W WISCONSIN AVE MSC 750', 'MAILING_ZIP': '532263518', 'MAILING_CITY': 'MILWAUKEE', 'MAILING_STATE': 'WI', 'LOCATION_ADDRESS': '9000 W WISCONSIN AVE MSC 750', 'LOCATION_ZIP': '532263518', 'LOCATION_CITY': 'MILWAUKEE', 'LOCATION_STATE': 'WI', 'UPDATED': '2007-07-08'}, {'CUSTOMER_KEY': '71238', 'NAME': "CHILDREN'S HOSPITAL OF WISCONSIN", 'NPI': 17808

[]
No results found
---
[]
No results found
---
[{'CUSTOMER_KEY': '51953', 'NAME': 'TRI STATE MEMORIAL HOSPITAL', 'NPI': 1124186804, 'TAXONOMY': 'Clinic/Center End-Stage Renal Disease (ESRD) Treatment', 'CATEGORY': 'Hospital', 'SUBPART': 'NO', 'MAILING_ADDRESS': 'PO BOX 189', 'MAILING_ZIP': '99403', 'MAILING_CITY': 'CLARKSTON', 'MAILING_STATE': 'WA', 'LOCATION_ADDRESS': '1221 HIGHLAND AVE', 'LOCATION_ZIP': '99403', 'LOCATION_CITY': 'CLARKSTON', 'LOCATION_STATE': 'WA', 'UPDATED': '2007-07-08'}]
---
[{'CUSTOMER_KEY': '51995', 'NAME': 'MOLINA HEALTHCARE', 'NPI': 1699207522, 'TAXONOMY': 'Exclusive Provider Organization', 'CATEGORY': 'Hospital', 'SUBPART': 'NO', 'MAILING_ADDRESS': '200 OCEANGATE STE 100', 'MAILING_ZIP': '908024317', 'MAILING_CITY': 'LONG BEACH', 'MAILING_STATE': 'CA', 'LOCATION_ADDRESS': '200 OCEANGATE STE 100', 'LOCATION_ZIP': '908024317', 'LOCATION_CITY': 'LONG BEACH', 'LOCATION_STATE': 'CA', 'UPDATED': '2017-03-30'}, {'CUSTOMER_KEY': '51995', 'NAME': 'MOLINA HEALTHCARE O

[]
No results found
---
[]
No results found
---
[{'CUSTOMER_KEY': '134657', 'NAME': 'AMERICAN MEDICAL ASSOCIATION', 'NPI': 1598762809, 'TAXONOMY': 'Specialist Research Data Abstracter/Coder', 'CATEGORY': 'Hospital', 'SUBPART': 'NO', 'MAILING_ADDRESS': '1529 WESTERHAM LOOP', 'MAILING_ZIP': '346557155', 'MAILING_CITY': 'TRINITY', 'MAILING_STATE': 'FL', 'LOCATION_ADDRESS': '1529 WESTERHAM LOOP', 'LOCATION_ZIP': '346557155', 'LOCATION_CITY': 'TRINITY', 'LOCATION_STATE': 'FL', 'UPDATED': '2007-07-08'}]
---
[]
No results found
---
[]
No results found
---
[]
No results found
---
[{'CUSTOMER_KEY': '55864', 'NAME': 'PRIMARY HEALTH NETWORK', 'NPI': 1275730202, 'TAXONOMY': 'Clinic/Center Federally Qualified Health Center (FQHC)', 'CATEGORY': 'Hospital', 'SUBPART': 'NO', 'MAILING_ADDRESS': '100 SHENANGO AVE', 'MAILING_ZIP': '161461503', 'MAILING_CITY': 'SHARON', 'MAILING_STATE': 'PA', 'LOCATION_ADDRESS': '2000 GREEN ST', 'LOCATION_ZIP': '161211307', 'LOCATION_CITY': 'FARRELL', 'LOCATION_STATE': 'P

...

[{'CUSTOMER_KEY': '58526', 'NAME': 'UK HEALTHCARE', 'NPI': 1902214448, 'TAXONOMY': 'General Acute Care Hospital', 'CATEGORY': 'Hospital', 'SUBPART': 'NO', 'MAILING_ADDRESS': '900 S LIMESTONE CTW 304', 'MAILING_ZIP': '405360001', 'MAILING_CITY': 'LEXINGTON', 'MAILING_STATE': 'KY', 'LOCATION_ADDRESS': '900 S LIMESTONE CTW 304', 'LOCATION_ZIP': '405360001', 'LOCATION_CITY': 'LEXINGTON', 'LOCATION_STATE': 'KY', 'UPDATED': '2014-09-29'}, {'CUSTOMER_KEY': '58526', 'NAME': 'UK HEALTHCARE', 'NPI': 1043740244, 'TAXONOMY': 'Pathology Anatomic Pathology', 'CATEGORY': 'Hospital', 'SUBPART': 'NO', 'MAILING_ADDRESS': '800 ROSE ST', 'MAILING_ZIP': '405367001', 'MAILING_CITY': 'LEXINGTON', 'MAILING_STATE': 'KY', 'LOCATION_ADDRESS': '800 ROSE ST', 'LOCATION_ZIP': '405367001', 'LOCATION_CITY': 'LEXINGTON', 'LOCATION_STATE': 'KY', 'UPDATED': '2017-06-20'}, {'CUSTOMER_KEY': '58526', 'NAME': 'UNIVERSITY OF KENTUCKY HOSPITAL', 'NPI': 1154519668, 'TAXONOMY': 'Internal Medicine', 'CATEGORY': 'Hospital', 'SUBP

[{'CUSTOMER_KEY': '54170', 'NAME': 'MAGNOLIA REGIONAL HEALTH CENTER', 'NPI': 1699756445, 'TAXONOMY': 'General Acute Care Hospital', 'CATEGORY': 'Hospital', 'SUBPART': 'NO', 'MAILING_ADDRESS': '611 ALCORN DR', 'MAILING_ZIP': '388349368', 'MAILING_CITY': 'CORINTH', 'MAILING_STATE': 'MS', 'LOCATION_ADDRESS': '611 ALCORN DR', 'LOCATION_ZIP': '388349368', 'LOCATION_CITY': 'CORINTH', 'LOCATION_STATE': 'MS', 'UPDATED': '2007-07-09'}, {'CUSTOMER_KEY': '54170', 'NAME': 'MAGNOLIA REGIONAL HEALTH CENTER', 'NPI': 1083103980, 'TAXONOMY': 'General Acute Care Hospital', 'CATEGORY': 'Hospital', 'SUBPART': 'NO', 'MAILING_ADDRESS': '1903 MEADOWBROOK RD APT 13', 'MAILING_ZIP': '388342433', 'MAILING_CITY': 'CORINTH', 'MAILING_STATE': 'MS', 'LOCATION_ADDRESS': '611 ALCORN DR', 'LOCATION_ZIP': '388349321', 'LOCATION_CITY': 'CORINTH', 'LOCATION_STATE': 'MS', 'UPDATED': '2018-05-07'}, {'CUSTOMER_KEY': '54170', 'NAME': 'MAGNOLIA REGIONAL HEALTH CENTER', 'NPI': 1063576247, 'TAXONOMY': 'Home Health', 'CATEGORY':

[{'CUSTOMER_KEY': '58975', 'NAME': 'YAKIMA VALLEY FARMWORKERS CLINIC', 'NPI': 1073722526, 'TAXONOMY': 'Pharmacist', 'CATEGORY': 'Hospital', 'SUBPART': 'NO', 'MAILING_ADDRESS': '215 S 11TH AVE', 'MAILING_ZIP': '98902', 'MAILING_CITY': 'YAKIMA', 'MAILING_STATE': 'WA', 'LOCATION_ADDRESS': '215 S 11TH AVE', 'LOCATION_ZIP': '989023248', 'LOCATION_CITY': 'YAKIMA', 'LOCATION_STATE': 'WA', 'UPDATED': '2009-10-29'}]
---
[{'CUSTOMER_KEY': '129438', 'NAME': 'PRESBYTERIAN HOSPITAL OF PLANO', 'NPI': 1073664116, 'TAXONOMY': 'Psychiatric Unit', 'CATEGORY': 'Hospital', 'SUBPART': 'NO', 'MAILING_ADDRESS': '6200 W PARKER RD', 'MAILING_ZIP': '750937939', 'MAILING_CITY': 'PLANO', 'MAILING_STATE': 'TX', 'LOCATION_ADDRESS': '6200 W PARKER RD', 'LOCATION_ZIP': '750937939', 'LOCATION_CITY': 'PLANO', 'LOCATION_STATE': 'TX', 'UPDATED': '2007-07-08'}]
---
[{'CUSTOMER_KEY': '53690', 'NAME': 'BLACKFEET COMMUNITY HOSPITAL', 'NPI': 1679693584, 'TAXONOMY': 'General Acute Care Hospital Rural', 'CATEGORY': 'Hospital', 

[{'CUSTOMER_KEY': '53112', 'NAME': 'OUR LADY OF THE LAKE PHYSICIAN GROUP LLC', 'NPI': 1184671455, 'TAXONOMY': 'Surgery', 'CATEGORY': 'Hospital', 'SUBPART': 'NO', 'MAILING_ADDRESS': '8415 GOODWOOD BLVD', 'MAILING_ZIP': '708067851', 'MAILING_CITY': 'BATON ROUGE', 'MAILING_STATE': 'LA', 'LOCATION_ADDRESS': '4950 ESSEN LN', 'LOCATION_ZIP': '708093738', 'LOCATION_CITY': 'BATON ROUGE', 'LOCATION_STATE': 'LA', 'UPDATED': '2013-02-20'}, {'CUSTOMER_KEY': '53112', 'NAME': 'OUR LADY OF THE LAKE PHYSICIAN GROUP LLC', 'NPI': 1356480214, 'TAXONOMY': 'Physician Assistant', 'CATEGORY': 'Hospital', 'SUBPART': 'YES', 'MAILING_ADDRESS': '2051 SILVERSIDE DR', 'MAILING_ZIP': '708089005', 'MAILING_CITY': 'BATON ROUGE', 'MAILING_STATE': 'LA', 'LOCATION_ADDRESS': '230 ROBERTS DR', 'LOCATION_ZIP': '707602661', 'LOCATION_CITY': 'NEW ROADS', 'LOCATION_STATE': 'LA', 'UPDATED': '2012-12-10'}, {'CUSTOMER_KEY': '53112', 'NAME': 'OUR LADY OF THE LAKE PHYSICIAN GROUP LLC', 'NPI': 1174662035, 'TAXONOMY': 'Physician Ass

[{'CUSTOMER_KEY': '52262', 'NAME': 'NW AMBULATORY SURGERY CENTER LLP', 'NPI': 1568423945, 'TAXONOMY': 'Clinic/Center Ambulatory Surgical', 'CATEGORY': 'Hospital', 'SUBPART': 'NO', 'MAILING_ADDRESS': '5215 HOLLISTER ST', 'MAILING_ZIP': '770406205', 'MAILING_CITY': 'HOUSTON', 'MAILING_STATE': 'TX', 'LOCATION_ADDRESS': '5215 HOLLISTER ST', 'LOCATION_ZIP': '770406205', 'LOCATION_CITY': 'HOUSTON', 'LOCATION_STATE': 'TX', 'UPDATED': '2007-07-08'}, {'CUSTOMER_KEY': '52262', 'NAME': 'NORTHWEST AMBULATORY SURGERY CENTER', 'NPI': 1902900616, 'TAXONOMY': 'Durable Medical Equipment & Medical Supplies', 'CATEGORY': 'Hospital', 'SUBPART': 'NO', 'MAILING_ADDRESS': '5215 HOLLISTER ST', 'MAILING_ZIP': '770406205', 'MAILING_CITY': 'HOUSTON', 'MAILING_STATE': 'TX', 'LOCATION_ADDRESS': '5215 HOLLISTER ST', 'LOCATION_ZIP': '770406205', 'LOCATION_CITY': 'HOUSTON', 'LOCATION_STATE': 'TX', 'UPDATED': '2007-07-08'}]
---
[]
No results found
---
[]
No results found
---
[{'CUSTOMER_KEY': '59064', 'NAME': 'MADISON

In [99]:
index = 0
new_list = []

In [85]:
orgs

Customer_Number                                       Company_Name  \
0             1627882                     Eastern Niagara Hospital, Inc.   
1             1672189                        Alaska Va Healthcare System   
2             1672234             Northern Arizona VA Health Care System   
3             1672354                           Harry S. Truman Memorial   
4             1921003                                   Vibra Healthcare   
...               ...                                                ...   
6900          4004623                        Center for Cosmetic Surgery   
6901          4006127  CORNERSTONE SURGERY CENTER & ANESTHESIA NURSIN...   
6902          4009224                          Hope Pregnancy Ministries   
6903       2501871519                                  Blue Care Network   
6904       3515911307                                   Cleveland Clinic   

     Attention First Attention Last                   Street 1ST Street 2ND  \
0                NaN            NaN                 521 East Ave        NaN   
1                NaN            NaN            1201 N Muldoon Rd        NaN   
2                NaN            NaN         500 N State Route 89        NaN   
3                NaN            NaN              800 Hospital Dr        NaN   
4              Kelly         Negley                 4550 Lena Dr        NaN   
...              ...            ...                          ...        ...   
6900             NaN            NaN  3023 Bunker Hill St Ste 204        NaN   
6901             NaN            NaN           10694 Magnolia Ave        NaN   
6902             NaN            NaN               1281 Burns Way        NaN   
6903         Felecia       Williams           28856 Lake Park Dr        NaN   
6904          Sunita     Srivastava            55 Fruit St # 440        NaN   

      Street 3RD              City State    Zipcode  Phone Number  \
0            NaN          Lockport    NY  140943201  716 514-5554   
1            NaN         Anchorage    AK  995046104  907 257-6791   
2            NaN          Prescott    AZ  863135001  928 717-7413   
3            NaN          Columbia    MO  652015275  573 814-6641   
4            NaN     Mechanicsburg    PA  170554920  615 550-7186   
...          ...               ...   ...        ...           ...   
6900         NaN         San Diego    CA  921095706           NaN   
6901         NaN         Riverside    CA  925051816           NaN   
6902         NaN         Kalispell    MT  599013109           NaN   
6903         NaN  Farmington Hills    MI  483312631           NaN   
6904         NaN            Boston    MA  021142621           NaN   

                Email Address  
0                         NaN  
1                         NaN  
2                         NaN  
3                         NaN  
4     KNEGLEY@VIBRAHEALTH.COM  
...                       ...  
6900                      NaN  
6901                      NaN  
6902                      NaN  
6903      FWILLIAMS@BCBSM.COM  
6904          SRIVASS@CCF.ORG  

[6905 rows x 12 columns]

In [93]:
orgs = orgs.fillna('None')

In [100]:
for row in orgs[index:].itertuples():
#     print(int(row.NPI))
    print('')
    zipcode = row.Zipcode[0:5]
    name = row.Company_Name.replace('.','')
    new_results = get_results(Search(name, row.State, row.City, zipcode))
    parsed = parse_results(new_results, row.Customer_Number)
    if not parsed:
        print('No results found')
        cus_name = name.replace('+','')+'*'
        new_results = get_results(Search(cus_name, row.State, row.City))
        parsed = parse_results(new_results, row.Customer_Number)
        if not parsed:
            print('ahh')
            new_results = get_results(Search("",row.State, row.City, row.Zipcode))
            parsed = parse_results(new_results, row.Customer_Number)
    new_list.append(parsed)
    if parsed:
        print(F'{row.Company_Name} matched to {parsed[0]["NAME"]}')
    else:
        print(F'{row.Company_Name} needs help')
    index += 1


Eastern Niagara Hospital, Inc. matched to EASTERN NIAGARA HOSPITAL, INC

No results found
ahh
Alaska Va Healthcare System matched to ANCHORAGE VAMC

No results found
ahh
Northern Arizona VA Health Care System matched to PRESCOTT VAMC

No results found
Harry S. Truman Memorial matched to HARRY S TRUMAN MEMORIAL VETERANS HOSPITAL

No results found
ahh
Vibra Healthcare matched to 8451 PEARL ST OPERATING COMPANY

No results found
ahh
Credentialsmart needs help

No results found
ahh
Northshore University Health System needs help

No results found
ahh
Wellmont Hancock County Hospital needs help

No results found
ahh
La Amistad Residential Tx Center matched to LA AMISTAD RESIDENTIAL TREATMENT CENTER , LLC

No results found
ahh
Bergman Eye Surgery  Center matched to BERGMAN EYE SURGERY CENTER, LLC

No results found
ahh
Community Hospital - Fairfax matched to COMMUNITY HOSPITAL ASSOCIATION

No results found
ahh
Federal Staffing Resources needs help

No results found
ahh
Ama Monitoring matched 

No results found
ahh
University Central Florida Health Services matched to COLLEGE OPTICAL EXPRESS FL INC.

No results found
ahh
Renaissance Surgery Center, LLC matched to HEALTHPLUS SURGERY CENTER LLC

No results found
ahh
Focus Healthcare of California matched to JDL HEALTHCARE INC

No results found
ahh
Delta Hills Health Corp. matched to GREENWOOD LEFLORE HOSPITAL

No results found
ahh
Healthcare Authority For Medical West matched to MEDICAL WEST IMAGING CENTER, LLC

No results found
ahh
Ameriwound, LLC needs help

No results found
ahh
Children's Medical Center (The) matched to CHILDRENS MEDICAL CENTER PHARMACY

No results found
ahh
Cimro needs help

No results found
ahh
Carolina Pines Reg Med Ctr matched to HARTSVILLE IMAGING ASSOCIATES LLP

No results found
ahh
Vail Valley Medical Center matched to VAIL SPORTS MEDICINE PHYSICAL THERAPY PC

No results found
ahh
Clearview Regional  Medical Center matched to MONROE HMA, LLC

No results found
ahh
Whittier Hospital Med. Center matched 

No results found
ahh
Rutgers Univ Health Services matched to RUTGERS, THE STATE UNIV

No results found
ahh
South Carolina Dept. of Mntl Hlth matched to SOUTH CAROLINA DEPT OF MENTAL HEALTH ACCOUNTING OFFICE

No results found
ahh
Southeast Alabama Rural Hlth Assoc. matched to SOUTHEAST ALABAMA RURAL HEALTH ASSOCIATES

No results found
ahh
Sherriff & Associates, Inc. matched to KATHLEEN J. KEENAN, PH.D., L.L.C.

No results found
ahh
Shawnee Health Services matched to SHAWNEE HEALTH SERVICE AND DEVELOPMENT CORP

No results found
ahh
MedAmerica/CA Emergency Phys Med Grp matched to CEP AMERICA ILLINOIS INTENSIVISTS

No results found
ahh
Lake PHO Inc. matched to COMMUNITY HOSPITALIST, LLC

No results found
ahh
Lakeland Behavorial Health System matched to LAKELAND HOSPITAL ACQUISITION CORPORATION, LLC

No results found
ahh
Muskegon County Community Mental Health matched to COUNTY OF MUSKEGON

No results found
ahh
Naval Ambulatory Care Center, Groton matched to NAVAL HEALTH CLINIC NEW ENGLAND


No results found
ahh
St. Vincent de Paul Healthcare Center needs help

No results found
ahh
VA Southern Oregon Rehabilitation Center & Clinics matched to WHITE CITY CBOC

No results found
ahh
Gainesville Urology ASC, LLC needs help

No results found
ahh
Absecon Long Term Care & Subacute matched to ABSECON MANOR NURSING HOME ASSOCS

No results found
ahh
Southern OB/GYN ASC matched to SOUTHERN OB GYN AMBULATORY SURGERY CENTER, INC

No results found
ahh
West Valley Hospital and Medical Center matched to PREMIERE PHYSICIANS INC

No results found
ahh
Jefferson General Hospital needs help

No results found
ahh
Monongahela Valley Assoc of Health Centers Inc matched to MONONGAHELA VALLEY ASSOCIATION OF HEALTH CENTERS INC

No results found
ahh
La Belle Vie Cosmetic Surgery Centers needs help

No results found
ahh
Westbury Health & Rehabilitation needs help

No results found
ahh
Sagamore Children's Psychiatric Center needs help

No results found
ahh
Univ. of Delaware Student Health Services need

ahh
Southwestern Pennsylvania Eye Surgery Center matched to E. RONALD SALVITTI, M.D., INC.

No results found
ahh
44 Gramercy GI OBS, PLLC needs help

No results found
ahh
California State University, Dominguez Hills needs help

No results found
ahh
CBC, LLC matched to ADVANCED PAIN CENTERS LLC

No results found
ahh
Kent County CMH Authority dba Network180 matched to SPECTRUM HEALTH CONTINUING CARE

No results found
ahh
Riverwalk Ambulatory Surgery Center, LLC matched to FUO LLC

No results found
ahh
Odd Fellow & Rebekah Rehab and HCC Inc. matched to ODD FELLOW AND REBEKAH REHABILITATION AND HEALTH CARE CENTER

No results found
ahh
Treasure Coast Surgical Center, Inc. matched to TREASURE COAST SURGICAL CENTER INC

No results found
ahh
Jacob Bornstein M.D., Harold N. Bornstein M.D., P.C. matched to BORNSTEIN & BORNSTEIN INC.

No results found
ahh
Norman Endoscopy Center LLC matched to NGA LAB SERVICES LLC

No results found
ahh
Fall Hill Gastroenterology Asso., Inc. matched to FALL HILL G

...

No results found
ahh
Endoscopy Consultants LLC needs help

No results found
ahh
Jackson & Coker - Licensing Board matched to THE KROGER CO

No results found
ahh
Baylor Scott & White Surgicare At Alliance matched to EXCEL SPORTS MEDICINE INSTITUTE AND ORTHOPEDIC INSTITUTE PLLC

No results found
ahh
Cvc Cardiac Cath Lab, Pllc matched to CVC CARDIAC CATH LAB PLLC

No results found
ahh
Nevada Air National Guard - Las Vegas needs help

No results found
ahh
Cancer Carepoint (Board) needs help

No results found
ahh
Medical Computer Business Services matched to STEPHEN W. BROWN AND RADIOLOGY ASSOCIATES OF AUGUSTA LLP

No results found
ahh
Moonlighting Solutions - Licensing Board needs help

No results found
ahh
Strand Endocrinology & Osteoporosis Center matched to GRAND STRAND SENIOR HEALTH CENTER, LLC

No results found
ahh
University of Florida Otolaryngology needs help

No results found
ahh
Argent Technologies, LLC needs help

No results found
ahh
Professional Billing and Management Services

ahh
Minnesota Urology P.A. matched to MINNESOTA ONCOLOGY HEMATOLOGY, PA

No results found
ahh
Jewish Renaissance Foundation matched to THE JEWISH RENAISSANCE FOUNDATION, INC.

No results found
ahh
Fort Bend Family Health Center d/b/a AccessHealth matched to FORT BEND FAMILY HEALTH CENTER, INC.

No results found
ahh
WakeMed Endoscopy-Midtown matched to TRIANGLE GASTROENTEROLOGY PLLC

No results found
ahh
Miami Jewish Health System, Inc matched to DOUGLAS GARDENS HOSPICE, INC.

No results found
ahh
Humble Vascular Surgical Center, Inc. matched to HUMBLE VASCULAR SURGICAL CENTER INC

No results found
ahh
New Look New Life Surgical Arts needs help

No results found
ahh
Teladoc Health - State Licensing Boards matched to HORIZON MENTAL HEALTH MANAGEMENT LLC

Physicians of Monmouth LLC. matched to PHYSICIANS OF MONMOUTH LLC

No results found
ahh
Newport Credentialing Solutions matched to FORT PAYNE RHC CORP

No results found
ahh
Hamilton Surgical Arts Surgery Center matched to FOLLAS CENTER F

No results found
ahh
The Vascular Center matched to ADVANCEXING PAIN AND REHABILITATION CLINIC PA

No results found
ahh
e2o Health matched to PERPETUAL DAYS HOSPICE, INC.

No results found
ahh
Beverly Hills Surgical Institute, LLC matched to DAVID RAMIN MD A PROFESSIONAL MEDICAL CORPORATION

No results found
ahh
Global Dynamics LLC needs help

No results found
ahh
Medical License Pro needs help

No results found
ahh
Surgery Center At Jensen Beach needs help

No results found
ahh
NeuGen needs help

No results found
ahh
Cicero Consulting Associates needs help

No results found
ahh
DNA Comprehensive Therapy Services LLC matched to DNA COMPREHENSIVE THERAPY SERVICES, LLC

No results found
ahh
Healthy Living needs help

No results found
ahh
Sun Valley Surgery Center LLC matched to STEVEN DELISLE DDS P.C.

No results found
ahh
Liberty Eye Surgical Center needs help

No results found
ahh
Surgery Center of York Road needs help

No results found
ahh
Kerlan Jobe Surgery Center matched to KERLAN-

No results found
ahh
Surgery Centers Of Excellence, Inc matched to MILAN S. CHAKRABARTY M.D. INC

No results found
ahh
Live Oak Clinic of Brazosport needs help

No results found
ahh
Third Eye Health matched to PATIENT INNOVATION CENTER NFP

No results found
ahh
All Care To You, LLC matched to ACCESS MEDICAL GROUP-SANTA MONICA INC.

No results found
ahh
First Physicians Capital Group needs help

No results found
ahh
None needs help

No results found
ahh
Surg Center of Belair matched to SURGCENTER OF BEL AIR

No results found
ahh
Southern Indiana ENT - Surgery matched to NEUROLOGY AND SLEEP SCIENCES, P.C.

No results found
ahh
SouthlandMD matched to SOUTHLAND OPTIM JENKINS EMERGENCY MEDICAL SERVICES, LLC

No results found
ahh
SLEEP ASSOCIATES OF FLORIDA, LLC matched to SLEEP ASSOCIATES OF FLORIDA LLC

No results found
ahh
Comprehensive Integrated Care matched to COMPREHENSIVE INTERVENTIONAL CARE CENTERS, PLLC

No results found
ahh
Iagnosis, Inc needs help

No results found
ahh
CONCILIO D

No results found
ahh
Hawthorne Surgery Center matched to SOCAL SURGERY CENTER LLC

No results found
ahh
Israel Schur MD, PLLC matched to PROVIDENCE INTERVENTIONAL ASSOCIATES, LLC

No results found
ahh
Frisco ASC, LLC matched to FRISCO ASC LLC

No results found
ahh
Pegasus Risk Management needs help

KLAMATH HEALTH PARTNERSHIP, INC. matched to KLAMATH HEALTH PARTNERSHIP, INC

No results found
ahh
Pancholi Cosmetic Surgery needs help

No results found
ahh
CTCA Shared Services Inc matched to MID AMERICA REHABILITATION CONSULTANTS INC

No results found
ahh
FCI SANDSTONE needs help

No results found
ahh
Andrews Institute Ambulatory Surgery Center matched to OGRADY ORTHOPAEDICS PL

No results found
ahh
Brella Advising matched to QV URGENT CARE TX PLLC

No results found
ahh
VA PREMIER needs help

No results found
ahh
San Vincente Surgery Center matched to WEST SURGERY CENTER

No results found
ahh
Easy Access Care IPA, Inc needs help

No results found
ahh
PRYMED MEDICAL CARE,INC. matched to PR

In [66]:
index

5740

In [45]:
orgs = orgs.fillna('None')

In [78]:
orgs = pd.read_csv("../../Data/Credentialling/Unmatched.csv")
orgs = orgs.rename(columns={'Customer Number': 'Customer_Number','Company Name': 'Company_Name','Zip Code': 'Zipcode'})

In [79]:
orgs.head()

Customer_Number                            Company_Name Attention First  \
0          1627882          Eastern Niagara Hospital, Inc.             NaN   
1          1672189             Alaska Va Healthcare System             NaN   
2          1672234  Northern Arizona VA Health Care System             NaN   
3          1672354                Harry S. Truman Memorial             NaN   
4          1921003                        Vibra Healthcare           Kelly   

  Attention Last            Street 1ST Street 2ND  Street 3RD           City  \
0            NaN          521 East Ave        NaN         NaN       Lockport   
1            NaN     1201 N Muldoon Rd        NaN         NaN      Anchorage   
2            NaN  500 N State Route 89        NaN         NaN       Prescott   
3            NaN       800 Hospital Dr        NaN         NaN       Columbia   
4         Negley          4550 Lena Dr        NaN         NaN  Mechanicsburg   

  State    Zipcode  Phone Number            Email Address  
0    NY  140943201  716 514-5554                      NaN  
1    AK  995046104  907 257-6791                      NaN  
2    AZ  863135001  928 717-7413                      NaN  
3    MO  652015275  573 814-6641                      NaN  
4    PA  170554920  615 550-7186  KNEGLEY@VIBRAHEALTH.COM

In [103]:
get_results(Search('EASTERN NIAGARA HOSPITAL*', 'NY','LOCKPORT','140943201'))

{'result_count': 3,
 'results': [{'enumeration_type': 'NPI-2',
   'number': 1063400539,
   'last_updated_epoch': 1468326087,
   'created_epoch': 1128902400,
   'basic': {'organization_name': 'EASTERN NIAGARA HOSPITAL, INC',
    'organizational_subpart': 'NO',
    'enumeration_date': '2005-10-10',
    'last_updated': '2016-07-12',
    'status': 'A',
    'authorized_official_credential': 'MBA, CPA',
    'authorized_official_first_name': 'MICHAEL',
    'authorized_official_last_name': 'ICKOWSKI',
    'authorized_official_middle_name': 'FRANCIS',
    'authorized_official_telephone_number': '716-514-5501',
    'authorized_official_title_or_position': 'CHIEF FINANCIAL OFFICER',
    'name': 'EASTERN NIAGARA HOSPITAL, INC',
    'authorized_official_name_prefix': 'MR.'},
   'other_names': [],
   'addresses': [{'country_code': 'US',
     'country_name': 'United States',
     'address_purpose': 'LOCATION',
     'address_type': 'DOM',
     'address_1': '521 EAST AVE',
     'address_2': '',
     'c

In [82]:
zz

{'result_count': 1,
 'results': [{'enumeration_type': 'NPI-2',
   'number': 1780615492,
   'last_updated_epoch': 1197244800,
   'created_epoch': 1152057600,
   'basic': {'organization_name': 'CITY OF CARIBOU',
    'organizational_subpart': 'NO',
    'enumeration_date': '2006-07-05',
    'last_updated': '2007-12-10',
    'status': 'A',
    'authorized_official_first_name': 'KRIS',
    'authorized_official_last_name': 'DOODY',
    'authorized_official_middle_name': 'A',
    'authorized_official_telephone_number': '207-498-1181',
    'authorized_official_title_or_position': 'CHEIF EXECUTIVE OFFICER',
    'authorized_official_name_prefix': 'MS.',
    'name': 'CITY OF CARIBOU'},
   'other_names': [{'organization_name': 'CARY MEDICAL CENTER',
     'code': '3',
     'type': 'Doing Business As'}],
   'addresses': [{'country_code': 'US',
     'country_name': 'United States',
     'address_purpose': 'LOCATION',
     'address_type': 'DOM',
     'address_1': '163 VAN BUREN RD',
     'address_2': '

In [68]:
better_list = []
for thing in new_list:
    if thing:
        for other_thing in thing:
            better_list.append(other_thing)

In [69]:
matched = pd.DataFrame(better_list)

In [54]:
len(orgs)

11412

In [70]:
matched_customers = list(matched['CUSTOMER_KEY'])

In [72]:
orgs[orgs['Customer_Number'].isin(matched_customers)==False]

Customer_Number                                       Company_Name  \
10             1627882                     Eastern Niagara Hospital, Inc.   
17             1672189                        Alaska Va Healthcare System   
19             1672234             Northern Arizona VA Health Care System   
20             1672354                           Harry S. Truman Memorial   
23             1921003                                   Vibra Healthcare   
...                ...                                                ...   
11405          4004623                        Center for Cosmetic Surgery   
11406          4006127  CORNERSTONE SURGERY CENTER & ANESTHESIA NURSIN...   
11408          4009224                          Hope Pregnancy Ministries   
11410       2501871519                                  Blue Care Network   
11411       3515911307                                   Cleveland Clinic   

      Attention First Attention Last                   Street 1ST Street 2ND  \
10               None           None                 521 East Ave       None   
17               None           None            1201 N Muldoon Rd       None   
19               None           None         500 N State Route 89       None   
20               None           None              800 Hospital Dr       None   
23              Kelly         Negley                 4550 Lena Dr       None   
...               ...            ...                          ...        ...   
11405            None           None  3023 Bunker Hill St Ste 204       None   
11406            None           None           10694 Magnolia Ave       None   
11408            None           None               1281 Burns Way       None   
11410         Felecia       Williams           28856 Lake Park Dr       None   
11411          Sunita     Srivastava            55 Fruit St # 440       None   

      Street 3RD              City State    Zipcode  Phone Number  \
10          None          Lockport    NY  140943201  716 514-5554   
17          None         Anchorage    AK  995046104  907 257-6791   
19          None          Prescott    AZ  863135001  928 717-7413   
20          None          Columbia    MO  652015275  573 814-6641   
23          None     Mechanicsburg    PA  170554920  615 550-7186   
...          ...               ...   ...        ...           ...   
11405       None         San Diego    CA  921095706          None   
11406       None         Riverside    CA  925051816          None   
11408       None         Kalispell    MT  599013109          None   
11410       None  Farmington Hills    MI  483312631          None   
11411       None            Boston    MA  021142621          None   

                 Email Address  
10                        None  
17                        None  
19                        None  
20                        None  
23     KNEGLEY@VIBRAHEALTH.COM  
...                        ...  
11405                     None  
11406                     None  
11408                     None  
11410      FWILLIAMS@BCBSM.COM  
11411          SRIVASS@CCF.ORG  

[6905 rows x 12 columns]

In [63]:
orgs[:9456]

Customer_Number                             Company_Name  \
0               13323                      Cary Medical Center   
1               17736           Amarillo VA Health Care System   
2               18125                  Mason District Hospital   
3               18760                        Woodlawn Hospital   
4              486394        Feather River Tribal Health, Inc.   
...               ...                                      ...   
9451          2105985  Healthcare Staffing Professionals, Inc.   
9452          2105986        Oregon Specialists Surgery Center   
9453          2105987     Palm Shores Behavioral Health Center   
9454          2105989               Lakeview Behavioral Health   
9455          2105994       Sukhdev S. Grover, M.D. Associates   

     Attention First Attention Last              Street 1ST  Street 2ND  \
0               None           None  163 Van Buren Rd Ste 1        None   
1               None           None    6010 W Amarillo Blvd        None   
2               None           None         615 N Promenade  PO Box 530   
3               None           None           1400 E 9th St        None   
4               None           None            2145 5th Ave        None   
...              ...            ...                     ...         ...   
9451            None           None  6914 Canby Ave Ste 109        None   
9452            None           None         2785 River Rd S        None   
9453            None           None         1324 37th Ave E        None   
9454            None           None     560 Cleburne Ter NE        None   
9455            None           None        2640 Pitcairn Rd        None   

     Street 3RD         City State    Zipcode  Phone Number  \
0          None      Caribou    ME  047363588  207 498-1227   
1          None     Amarillo    TX  791061990  806 355-9703   
2          None       Havana    IL  626440530  309 543-8579   
3          None    Rochester    IN  469758937  574 224-1173   
4          None     Oroville    CA  959655870  530 534-5394   
...         ...          ...   ...        ...           ...   
9451       None       Reseda    CA  913358736  818 921-3121   
9452       None        Salem    OR  973025883  614 562-9917   
9453       None    Bradenton    FL  342084555  941 792-2222   
9454       None      Atlanta    GA  303071422  678 713-2520   
9455       None  Monroeville    PA  151463309  724 275-1234   

               Email Address  
0     COUELLETTE@CARYMED.ORG  
1                       None  
2                       None  
3                       None  
4                       None  
...                      ...  
9451                    None  
9452                    None  
9453                    None  
9454                    None  
9455                    None  

[9456 rows x 12 columns]

In [75]:
matched.to_csv('../../Data/Credentialling/NPI_Customer_Address_Match.csv', index=False)

In [105]:
len(new_list)

6905

In [109]:
new_list

[[{'CUSTOMER_KEY': 1627882,
   'NAME': 'EASTERN NIAGARA HOSPITAL, INC',
   'OTHER_NAME': 'None',
   'NPI': 1063400539,
   'TAXONOMY': 'Clinic/Center End-Stage Renal Disease (ESRD) Treatment',
   'SUBPART': 'NO',
   'MAILING_ADDRESS': '521 EAST AVE',
   'MAILING_ZIP': '140943201',
   'MAILING_CITY': 'LOCKPORT',
   'MAILING_STATE': 'NY',
   'LOCATION_ADDRESS': '521 EAST AVE',
   'LOCATION_ZIP': '140943201',
   'LOCATION_CITY': 'LOCKPORT',
   'LOCATION_STATE': 'NY',
   'UPDATED': '2016-07-12'}],
 [{'CUSTOMER_KEY': 1672189,
   'NAME': 'ANCHORAGE VAMC',
   'OTHER_NAME': 'None',
   'NPI': 1417909011,
   'TAXONOMY': 'General Acute Care Hospital',
   'SUBPART': 'NO',
   'MAILING_ADDRESS': '1201 N MULDOON RD',
   'MAILING_ZIP': '995046104',
   'MAILING_CITY': 'ANCHORAGE',
   'MAILING_STATE': 'AK',
   'LOCATION_ADDRESS': '1201 N MULDOON RD',
   'LOCATION_ZIP': '995046104',
   'LOCATION_CITY': 'ANCHORAGE',
   'LOCATION_STATE': 'AK',
   'UPDATED': '2011-07-22'},
  {'CUSTOMER_KEY': 1672189,
   'NAM

In [110]:
other_list = []
for thing in new_list:
    for thing_2 in thing:
        other_list.append(thing_2)

In [133]:
new_matched = pd.DataFrame(other_list)

In [136]:
one_more_time = orgs[orgs.Customer_Number.isin(new_matched['CUSTOMER_KEY'])==False]

In [137]:
one_more_time

Customer_Number                      Company_Name Attention First  \
5             1922461                   Credentialsmart            None   
7             2100452  Wellmont Hancock County Hospital            None   
11            2100464        Federal Staffing Resources            None   
21            2084315        Emergency Medical Services            None   
27            2084343         St. Mary’s Medical Center           Karen   
...               ...                               ...             ...   
6888          3912089       Spectrum Services Group Inc            None   
6891          3919877        Innovative Health Services            None   
6892          3926197                    Healthlabs.com            None   
6896          3991990                    ASC Assist LLC            None   
6903       2501871519                 Blue Care Network         Felecia   

     Attention Last                   Street 1ST  Street 2ND Street 3RD  \
5              None     1560 Sherman Ave Ste 860        None       None   
7              None                 1519 Main St  PO Box 216       None   
11             None   2200 Somerville Rd Ste 300        None       None   
21             None          920 Main St Ste 300        None       None   
27            Blair           201 NW R D Mize Rd        None       None   
...             ...                          ...         ...        ...   
6888           None  3841 N Freeway Blvd Ste 120        None       None   
6891           None                   PO Box 778        None       None   
6892           None  11150 S Wilcrest Dr Ste 200        None       None   
6896           None         63 Lake Diamond Blvd        None       None   
6903       Williams           28856 Lake Park Dr        None       None   

                  City State    Zipcode  Phone Number          Email Address  
5             Evanston    IL  602014808          None                   None  
7           Sneedville    TN  378690216  423 733-5006                   None  
11           Annapolis    MD  214013713  410 990-0795                   None  
21         Kansas City    MO  641052008  816 559-6312                   None  
27        Blue Springs    MO  640142533  816 943-3057  KBLAIR@CARONDELET.COM  
...                ...   ...        ...           ...                    ...  
6888        Sacramento    CA  958341968          None                   None  
6891            Easton    MD  216018914          None                   None  
6892           Houston    TX  770994343          None                   None  
6896             Ocala    FL  344725006          None                   None  
6903  Farmington Hills    MI  483312631          None    FWILLIAMS@BCBSM.COM  

[1378 rows x 12 columns]

In [127]:
listy =[]

In [129]:
for row in one_more_time.itertuples():
#     print(int(row.NPI))
    print('')
    zipcode = row.Zipcode[0:5]
    name = row.Company_Name.replace('.','')
    last_word = name.split(' ')[-1]
    name = name.replace(' '+last_word,'')+'*'
    new_results = get_results(Search(name, row.State, row.City, zipcode))
    parsed = parse_results(new_results, row.Customer_Number)
    if not parsed:
        print('No results found')
    listy+=parsed
    if parsed:
        print(F'{row.Company_Name} matched to {parsed[0]["NAME"]}')
    else:
        print(F'{row.Company_Name} needs help')


No results found
Credentialsmart needs help

Northshore University Health System matched to NORTHSHORE UNIVERSITY HEALTHSYSTEM

No results found
Wellmont Hancock County Hospital needs help

No results found
Federal Staffing Resources needs help

Summit Healthcare Regional Med Ctr matched to SUMMIT HEALTHCARE ASSOCIATION

No results found
Emergency Medical Services needs help

No results found
St. Mary’s Medical Center needs help

No results found
Hunterdon HealthCare Partners needs help

No results found
Ethica Health and Retirement Communities needs help

No results found
Presbyterian Hospital of Allen needs help

No results found
Health Alliance of the Hudson Valley Mary's Ave Campus needs help

No results found
Northwest MS Regional Medical Center needs help

No results found
Cottage Health System needs help

No results found
InGenesis, Inc. needs help

Florida Hospital Cvo matched to UNIVERSITY COMMUNITY HOSPITAL, INC

No results found
Barton  Associates needs help

No results fou

Jacksonville Hospital matched to JACKSONVILLE ANESTHESIA LLC

No results found
St. Joseph's Hospital & Medical Center needs help

No results found
Harbor Health Plan/Trusted Health Plan needs help

No results found
Molina Healthcare needs help

No results found
AddVal needs help

No results found
Vista Staffing Solutions needs help

No results found
Cypress Healthcare Consultants needs help

No results found
Partners In Pediatrics needs help

No results found
Pinnacle Health Group needs help

No results found
St. Marys Health Center needs help

No results found
Omni IPA/Medcore Medical Group needs help

No results found
Daniel & Yeager/ D&Y needs help

No results found
Health Smart Management Services Organization needs help

No results found
HealthPlus of Michigan needs help

No results found
Queens Endoscopy ASC, LLC needs help

No results found
Desert Physician Association needs help

No results found
Stat Radiology needs help

No results found
V.A. Medical Center needs help

No res

No results found
Health Help, Inc. needs help

Endoscopy Center of LI matched to ENDOSCOPY CENTER OF LONG ISLAND LLC

No results found
Cityview Surgery Center needs help

No results found
West Michigan Physicians Network needs help

No results found
West Virginia University Health System needs help

No results found
Vassar Brothers  Medical Center needs help

No results found
Affiliated Doctors of Orange County needs help

No results found
Tiopa, Inc needs help

No results found
Independent Professional Services needs help

No results found
North Alabama Managed Care needs help

No results found
Professional Cred Verif Svc needs help

No results found
Western Healthcare needs help

No results found
Leslie A. Gallant, LLC needs help

No results found
Healthcare Business Solutions needs help

No results found
California Department of Veterans Affairs needs help

Great River Med Ctr matched to GREAT RIVER MEDICAL CENTER

Cape Surgery Center LLC matched to CAPE SURGERY CENTER, LLC

No resu

No results found
Blue Cross and Blue Shield of Tennessee needs help

No results found
Beacon Health Strategies, LLC needs help

No results found
Ark-La-Tex Health Network needs help

Guthrie Medical Group, PC matched to GUTHRIE MEDICAL GROUP, LTD.

No results found
Heartland Health Alliance needs help

No results found
Boston Medical Center/ Healthnet Plan needs help

No results found
Trinity Mother Frances Health System needs help

No results found
MVP Health Plan needs help

No results found
Quality Care Partners needs help

No results found
St . Mary's of Michigan needs help

No results found
Physicians of East Texas, LLC needs help

No results found
Managed Health Resources needs help

No results found
Precision Credentialing Services needs help

Baptist Health Plan matched to BAPTIST HEALTH MEDICAL GROUP INC

No results found
Fox Valley Medicine, Ltd needs help

No results found
Health First of Texas, Pa needs help

Rural Health Inc. matched to RURAL HEALTH, INC

No results found


No results found
Univ. of Michigan needs help

San Diego Outpatient ASC matched to SDOSC, LP

No results found
Sono Bello – Aesthetic Physicians, PC needs help

No results found
Ls Medical Staff Services Consulting needs help

No results found
Valor Network  Inc. needs help

No results found
Southern California Med. Gastroenterology Group, Inc. needs help

No results found
New Jersey Center For Ent Disorders needs help

No results found
Eastside Endoscopy Center needs help

No results found
Digestive Disease Specialists, Inc. needs help

No results found
Select Specialty Hospital-Ft Smith needs help

No results found
Worcester Surgical Center needs help

No results found
Healthhelp LLC needs help

No results found
None needs help

No results found
QTC Medical Management needs help

No results found
Quality Health Plans, Inc needs help

No results found
CHI Baylor St. Luke’s Medical Center needs help

No results found
Credentialing Specialist of America needs help

No results found
Wisc

...

No results found
Supertest needs help

No results found
xyztest needs help

No results found
societytest needs help

No results found
Lakeview Surgery Center needs help

No results found
Harvardstreet neighborhood health center needs help

No results found
Ambulatory Surgery Center of Killeen needs help

No results found
Alta Bates Medical Center needs help

No results found
Texas Tech University HSC at Amarillo needs help

Laurelwood Hospital matched to LAURELWOOD ASSOCIATES INC

Rockland Children's Psychiatric Ctr matched to ROCKLAND CHILDREN'S PSYCHIATRIC CENTER

Eye Surgery Center Ltd matched to EYE SURGERY CENTER LLC

No results found
Harbor Medical Associates, PC needs help

No results found
Gastroenterology Associates/Louisiana Endoscopy Center, Inc. needs help

No results found
War Memorial Hospital needs help

No results found
VA Hudson Valley Healthcare System needs help

No results found
Shriners Hospital For Children needs help

No results found
Advanced Family Surgery Urge

No results found
Fusion HealthCare Staffing needs help

No results found
OnCall EM Physicians, PLLC needs help

No results found
Horizon Health Consultants needs help

No results found
Solutions Through Innovative Technologies, Inc. needs help

No results found
TRI PARISH REHABILITATION HOSPITAL needs help

No results found
PacificSource needs help

No results found
Owensboro Community Health Network needs help

No results found
Johnsons Consulting, LLC needs help

No results found
Credentialing Board Test needs help

No results found
LEGACY PERSONNEL, INC. needs help

No results found
Physician Licensing Service needs help

Utah DOPL matched to UTAH HEALTH & HUMAN RIGHTS PROJECT

No results found
Weatherby Healthcare Licensing needs help

Nebraska Medicine matched to NEBRASKA MEDICAL CENTER

No results found
Professional Disability Associates needs help

No results found
EZDoctor needs help

No results found
McLean Ambulatory Surgery, LLC needs help

No results found
Federal Correctio

No results found
Consortium of Independent Immunology Clinics needs help

No results found
LN Credentialing, LLC needs help

No results found
Center for Advanced Reproductive Services, PC needs help

Advantage Locums matched to ADVANTAGE COUNSELING SERVICES

No results found
Healthcare Staffing Professionals, Inc. needs help

No results found
Lakeview Behavioral Health needs help

No results found
Advanced Plastic Surgery NYC needs help

No results found
Fcc Lompoc needs help

No results found
The Willough at Naples needs help

Wartburg Home (The) matched to WARTBURG HOME OF THE EVANGELICAL LUTHERAN CHURCH

No results found
Denton County Medical Society needs help

No results found
FCI Dublin needs help

No results found
FCC Hazelton needs help

No results found
Centinela Valley Endoscopy Center, Inc needs help

No results found
BOP-MDC Guaynabo needs help

No results found
CMU College of Medicine needs help

No results found
Sonoma State University Sports Medicine needs help

No resul

No results found
Mercy Ambulatory Surgical Center of Dallas needs help

No results found
Tqm Government Solutions needs help

No results found
Physicians Health Plan needs help

No results found
Dvantongerenllc needs help

No results found
Atlas Credentialing Solutions needs help

No results found
UPMC Stroke Institute (Board) needs help

No results found
Pennsylvania Vascular Institute needs help

No results found
Lumeris Healthcare Outcomes LLC needs help

No results found
Mutual of Omaha needs help

No results found
Align Staffing needs help

No results found
Millennium Medical Group needs help

Patronus Holdings matched to PATRONUS PHYSICIANS GROUP PC

New York Life matched to NEW YORK AESTHETIC SURGERY, PC

Endoscopy Consultants LLC matched to ENDOSCOPY CONSULTANTS, LLC

No results found
Nevada Air National Guard - Las Vegas needs help

No results found
Cancer Carepoint (Board) needs help

No results found
Moonlighting Solutions - Licensing Board needs help

University of Florida 

No results found
Vulcan Imaging Associates needs help

North Jersey Dermatology Center, PC matched to NORTH JERSEY DERMATOLOGY CENTER, P.C.

No results found
Langtree Endoscopy Center needs help

No results found
Beacon Surgery Center needs help

No results found
Pacific Crest Healthcare Independent Provider Association, Inc. needs help

No results found
Skin and Cancer of Arizona needs help

No results found
Cowell Center Student Health Services needs help

No results found
Platinum Locums needs help

No results found
Reproductive Health and Wellness Center needs help

No results found
ICNA Relief Medical Clinic needs help

No results found
NCW Staffing needs help

No results found
Pegasus Risk Management needs help

No results found
Pancholi Cosmetic Surgery needs help

No results found
FCI SANDSTONE needs help

VA PREMIER matched to VALOR HEALTH CARE SERVICE, INC

No results found
Easy Access Care IPA, Inc needs help

No results found
Ortho Spine Surgical LLC needs help

No results 

In [256]:
philly = pd.read_csv('../../Data/Credentialling/Philly_Place.csv')

In [274]:
x_list = []
bopp = []
for row in philly[12:].itertuples():
    print(' ')
    print(' ')
    print(row.CUSTOMER_NAME)
    x = Search(row.CUSTOMER_NAME+'*', row.State,row.City,row.Short_Zip, 'GENERAL ACUTE*')
    x_list.append(x)
    bopp+=parse_results(get_results(x), row.CUSTOMER_NAME)

 
 
Rockford Center
 
 
Suburban Community Hospital
 
 
Roxborough Memorial Hospital
 
 
Lower Bucks Hospital
 
 
Fairmount Behavioral Health System
 
 
Mercy Health System
 
 
Jeanes Hospital
 
 
Drexel University
 
 
Delaware Psychiatric Center
 
 
Thomas Jefferson University
 
 
Temple University Hospital
 
 
Grand View Hospital
 
 
Main Line Health Hospitals
 
 
Virtua Health-West Jersey
 
 
Inspira Medical Center Woodbury
 
 
Upper Bay Surgery Center, Llc
 
 
Orthopaedic Specialists
 
 
Burlington County Endoscopy Center
 
 
Thomas Jefferson University Hospital
 
 
Kennedy Health System
 
 
Crozer-Chester Medical  Center
 
 
Va Medical Center
 
 
Fox Chase Cancer
 
 
Deborah Heart And Lung Center
 
 
Grand View Surgery Center At Harleysville
 
 
Rothman Specialty Hospital
 
 
Salem Medical Center
 
 
The Children'S Hospital Of Philadelphia
 
 
Philadelphia Va Medical Center
 
 
Center For Family Guidance, Pc
 
 
Eye Surgery Center Of Chester County
 
 
Physicians Care Surgical Hos

In [502]:
number = 89
x_list[number]

Search(organization_name='Camcare Health Corporation*', state='NJ', city='Camden', postal_code=8103, taxonomy_desc='GENERAL ACUTE*', version='2.1', enumeration_type='NPI-2')

In [503]:
# x_list[number].organization_name='best impression*'
x_list[number].postal_code='08103'
x_list[number].taxonomy_desc=''
# x_list[number].city='Philadelphia'
this = x_list[number]
get_results(this)

{'result_count': 8,
 'results': [{'enumeration_type': 'NPI-2',
   'number': 1538338090,
   'last_updated_epoch': 1426118400,
   'created_epoch': 1204156800,
   'basic': {'organization_name': 'CAMCARE HEALTH CORPORATION',
    'organizational_subpart': 'NO',
    'enumeration_date': '2008-02-28',
    'last_updated': '2015-03-12',
    'status': 'A',
    'authorized_official_first_name': 'SALIMAH',
    'authorized_official_last_name': 'POLLARD',
    'authorized_official_telephone_number': '856-583-2415',
    'authorized_official_title_or_position': 'ASST. DIRECTOR OF PATIENT ACCOUNTS',
    'authorized_official_name_prefix': 'MRS.',
    'name': 'CAMCARE HEALTH CORPORATION'},
   'other_names': [],
   'addresses': [{'country_code': 'US',
     'country_name': 'United States',
     'address_purpose': 'LOCATION',
     'address_type': 'DOM',
     'address_1': '1315 N DELAWARE ST',
     'address_2': '',
     'city': 'PAULSBORO',
     'state': 'NJ',
     'postal_code': '080661367',
     'telephone_n

In [131]:
len(listy)

634

In [132]:
other_list+=listy

In [135]:
new_matched.drop_duplicates('CUSTOMER_KEY')

CUSTOMER_KEY                                       NAME  \
0           1627882              EASTERN NIAGARA HOSPITAL, INC   
1           1672189                             ANCHORAGE VAMC   
4           1672234                              PRESCOTT VAMC   
7           1672354  HARRY S TRUMAN MEMORIAL VETERANS HOSPITAL   
8           1921003            8451 PEARL ST OPERATING COMPANY   
...             ...                                        ...   
22673       3570435      PREGNANCY RESOURCE CENTER OF GWINNETT   
22674       3579739                     MEDICAL EVALUATORS INC   
22675       3696356      NORTH JERSEY DERMATOLOGY CENTER, P.C.   
22677       3774744             VALOR HEALTH CARE SERVICE, INC   
22679       3907610                  GLOBAL HEALTH CONSULTANTS   

                 OTHER_NAME         NPI  \
0                      None  1063400539   
1                      None  1417909011   
4                      None  1275583684   
7                      None  1275836488   
8                      None  1902882178   
...                     ...         ...   
22673  OBRIA MEDICAL CLINIC  1942834411   
22674          GULF IMAGING  1679561526   
22675                  None  1932237476   
22677                  None  1396185013   
22679                  None  1235514647   

                                                TAXONOMY SUBPART  \
0      Clinic/Center End-Stage Renal Disease (ESRD) T...      NO   
1                            General Acute Care Hospital      NO   
4                            General Acute Care Hospital      NO   
7                            General Acute Care Hospital      NO   
8                               Skilled Nursing Facility      NO   
...                                                  ...     ...   
22673                     Clinic/Center Community Health      NO   
22674               Clinic/Center Radiology, Mammography      NO   
22675                       Dermatology Dermatopathology     YES   
22677                        Community/Behavioral Health      NO   
22679                                    Family Medicine      NO   

            MAILING_ADDRESS MAILING_ZIP   MAILING_CITY MAILING_STATE  \
0              521 EAST AVE   140943201       LOCKPORT            NY   
1         1201 N MULDOON RD   995046104      ANCHORAGE            AK   
4              PO BOX 94411   441014411      CLEVELAND            OH   
7           800 HOSPITAL DR   652015275       COLUMBIA            MO   
8              4550 LENA DR   170554920  MECHANICSBURG            PA   
...                     ...         ...            ...           ...   
22673   565 OLD NORCROSS RD       30046  LAWRENCEVILLE            GA   
22674         406 W 19TH ST   324054602    PANAMA CITY            FL   
22675      35 GREEN POND RD   078662013       ROCKAWAY            NJ   
22677   4701 COX RD STE 301   230606802     GLEN ALLEN            VA   
22679  7720 SPENCER HIGHWAY   775051866       PASADENA            TX   

           LOCATION_ADDRESS LOCATION_ZIP  LOCATION_CITY LOCATION_STATE  \
0              521 EAST AVE    140943201       LOCKPORT             NY   
1         1201 N MULDOON RD    995046104      ANCHORAGE             AK   
4          500 N HIGHWAY 89    863135001       PRESCOTT             AZ   
7           800 HOSPITAL DR    652015275       COLUMBIA             MO   
8             8451 PEARL ST    802294804       THORNTON             CO   
...                     ...          ...            ...            ...   
22673   565 OLD NORCROSS RD        30046  LAWRENCEVILLE             GA   
22674         406 W 19TH ST    324054602    PANAMA CITY             FL   
22675      35 GREEN POND RD    078662013       ROCKAWAY             NJ   
22677   4701 COX RD STE 301    230606802     GLEN ALLEN             VA   
22679  7720 SPENCER HIGHWAY    775051866       PASADENA             TX   

          UPDATED  
0      2016-07-12  
1      2011-07-22  
4      2017-11-01  
7      2010-12-09  
8      2007-07-09  
...   

In [138]:
orgs_2 = pd.read_csv("../../Data/Credentialling/NPI_Customer_Address_Match.csv")

In [140]:
all_things = pd.concat([orgs_2, new_matched])

In [143]:
solos = all_things.drop_duplicates('CUSTOMER_KEY', keep=False)
dupos = all_things[all_things.CUSTOMER_KEY.isin(solos.CUSTOMER_KEY)==False]

In [145]:
dupos[dupos.CUSTOMER_KEY==2106006]

CUSTOMER_KEY                         NAME       OTHER_NAME         NPI  \
5        2106006  CITRUS HEALTH NETWORK, INC.             None  1649367970   
6        2106006  CITRUS HEALTH NETWORK, INC.             None  1871675397   
7        2106006  CITRUS HEALTH NETWORK, INC.  CITRUS PHARMACY  1962592915   
8        2106006  CITRUS HEALTH NETWORK, INC.             None  1982744975   
9        2106006  CITRUS HEALTH NETWORK, INC.             None  1093855124   
10       2106006  CITRUS HEALTH NETWORK, INC.             None  1992081178   
11       2106006  CITRUS HEALTH NETWORK, INC.             None  1982975082   
12       2106006  CITRUS HEALTH NETWORK, INC.             None  1982964581   
13       2106006  CITRUS HEALTH NETWORK, INC.             None  1497094890   

                                             TAXONOMY SUBPART  \
5                            Public Health or Welfare      NO   
6                            Pharmacy Clinic Pharmacy      NO   
7                                            Pharmacy      NO   
8                                     Case Management      NO   
9   Community Based Residential Treatment Facility...      NO   
10                        Community/Behavioral Health      NO   
11  Clinic/Center Federally Qualified Health Cente...      NO   
12  Clinic/Center Federally Qualified Health Cente...      NO   
13                 Early Intervention Provider Agency      NO   

    MAILING_ADDRESS MAILING_ZIP MAILING_CITY MAILING_STATE  \
5   4175 W 20TH AVE   330125874      HIALEAH            FL   
6   4175 W 20TH AVE   330125874      HIALEAH            FL   
7   4175 W 20TH AVE   330125874      HIALEAH            FL   
8   4175 W 20TH AVE   330125874      HIALEAH            FL   
9   4175 W 20TH AVE   330125874      HIALEAH            FL   
10  4175 W 20TH AVE   330125874      HIALEAH            FL   
11  4175 W 20TH AVE   330125874      HIALEAH            FL   
12  4175 W 20TH AVE   330125874      HIALEAH            FL   
13  4175 W 20TH AVE   330125874      HIALEAH            FL   

         LOCATION_ADDRESS LOCATION_ZIP   LOCATION_CITY LOCATION_STATE  \
5         4175 W 20TH AVE    330125874         HIALEAH             FL   
6         4175 W 20TH AVE    330125874         HIALEAH             FL   
7         4175 W 20TH AVE    330125874         HIALEAH             FL   
8         4175 W 20TH AVE    330125874         HIALEAH             FL   
9         4175 W 20TH AVE    330125874         HIALEAH             FL   
10  12550 SW 282ND STREET        33033       HOMESTEAD             FL   
11          705 E 26TH ST    330133823         HIALEAH             FL   
12         8375 S PALM DR    330254535  PEMBROKE PINES             FL   
13        4175 W 20TH AVE    330125874         HIALEAH             FL   

       UPDATED  
5   2007-07-08  
6   2007-07-09  
7   2015-09-30  
8   2007-07-09  
9   2007-07-09  
10  2011-11-01  
11  2012-01-20  
12  2012-08-07  
13  2013-02-05

In [148]:
org_addresses = pd.read_excel('../../Data/Credentialling/Org_Addresses.xlsx')

In [152]:
customers = pd.read_csv('../../Data/Credentialling/Customers.csv')

In [172]:
cust_list

[105762,
 1051645,
 1246802,
 1628000,
 1662109,
 1672189,
 1750569,
 1995109,
 1997743,
 2000868,
 2003364,
 2006464,
 2006596,
 2040899,
 2044183,
 2051067,
 2053294,
 2079895,
 2079912,
 2079915,
 2079917,
 2079926,
 2079929,
 2079931,
 2079933,
 2079937,
 2079941,
 2079942,
 2079949,
 2079982,
 2080002,
 2080016,
 2080042,
 2080046,
 2080057,
 2080059,
 2080063,
 2080070,
 2080091,
 2080092,
 2080104,
 2080112,
 2080130,
 2080131,
 2080140,
 2080142,
 2080150,
 2080151,
 2080155,
 2080171,
 2080187,
 2080197,
 2080200,
 2080212,
 2080219,
 2080220,
 2080241,
 2080242,
 2080260,
 825329,
 951717,
 968540,
 1662198,
 1672234,
 1950005,
 1997741,
 2041391,
 2074675,
 2077717,
 2079907,
 2079916,
 2079927,
 2079935,
 2079943,
 2079961,
 2079974,
 2079976,
 2079993,
 2080013,
 2080022,
 2080025,
 2080043,
 2080069,
 2080089,
 2080114,
 2080118,
 2080139,
 2080152,
 2080157,
 2080186,
 2080195,
 2080204,
 2080211,
 2080228,
 2080235,
 2080240,
 17736,
 439902,
 486394,
 577557,
 1662165,

In [178]:
try_1 = ATTEMPTS[ATTEMPTS.CUSTOMER_NBR==1051645][['CUSTOMER_NAME',
       'CUSTOMER_CATEGORY_DESC',
       'Street 1ST', 'City', 'State', 'Zip Code',
       'NAME',
       'OTHER_NAME', 'NPI', 'TAXONOMY', 'SUBPART', 'MAILING_ADDRESS',
       'MAILING_ZIP', 'MAILING_CITY', 'MAILING_STATE', 'LOCATION_ADDRESS',
       'LOCATION_ZIP', 'LOCATION_CITY', 'LOCATION_STATE', 'UPDATED']]

In [156]:
CUSTOMER = pd.merge(customers, org_addresses, left_on='CUSTOMER_NBR',right_on='Customer Number')

In [159]:
ATTEMPTS = pd.merge(CUSTOMER, dupos, left_on='CUSTOMER_NBR', right_on='CUSTOMER_KEY', suffixes = ['','_NBR'])

In [162]:
cust_list = list(ATTEMPTS.CUSTOMER_NBR.unique())

In [176]:
ATTEMPTS = ATTEMPTS.sort_values('UPDATED', ascending=False)

In [195]:
listie = []
for number in cust_list:
    print('')
    new_df = ATTEMPTS[ATTEMPTS.CUSTOMER_NBR==number]
    new_df = new_df.drop_duplicates(subset = ['NPI'])
    print(len(new_df))
    if list(new_df[0:1]['CUSTOMER_CATEGORY_DESC'])[0]=='Hospital':
        new_df = new_df[new_df.TAXONOMY=='GENERAL_ACUTE_CARE_HOSPITAL']
    print(len(new_df))
    if len(new_df)>1:
        new_df = new_df[new_df.SUBPART=='NO']
    if len(new_df)>0:
        new_dict ={
            'CUSTOMER_NBR': number,
            'NPI': list(new_df[0:1]['NPI'])[0]
        }
        listie.append(new_dict)


10
0

5
0

3
0

4
0

2
0

3
3

8
0

10
0

10
0

10
0

7
0

10
0

2
0

10
0

10
0

10
0

4
0

2
2

10
0

10
0

10
0

9
0

5
0

10
0

2
2

10
0

2
2

3
3

6
6

10
10

4
4

10
0

10
10

2
0

10
0

10
0

10
0

2
0

7
0

2
0

2
0

4
4

3
0

7
0

10
0

10
10

10
0

2
2

10
0

4
0

10
0

2
0

2
0

10
10

10
0

10
0

5
0

8
0

2
0

7
0

8
0

10
0

5
0

3
0

10
0

6
6

2
0

2
0

10
0

2
0

9
0

10
0

10
0

2
2

3
0

9
0

10
10

10
0

10
0

6
0

4
0

10
10

10
0

5
0

5
0

10
0

3
0

10
0

4
4

2
0

3
0

2
0

3
0

2
2

10
0

2
0

2
0

2
0

2
2

3
0

2
0

2
0

2
0

9
0

2
0

10
0

10
0

4
0

3
0

9
9

4
0

4
0

10
0

4
0

4
0

10
10

10
0

5
5

10
0

6
0

10
0

5
5

7
0

2
2

10
0

3
0

5
0

9
9

2
0

10
0

2
0

10
0

5
0

10
0

2
0

10
10

6
0

10
0

10
0

2
0

3
0

5
0

10
0

10
0

3
0

10
10

3
0

2
0

6
0

2
0

10
0

10
0

5
0

7
0

5
0

6
0

4
0

5
5

5
5

10
0

3
0

2
2

10
0

6
0

4
4

10
0

4
0

5
0

10
0

7
0

2
2

3
0

10
0

4
0

6
0

2
0

10
0

5
0

8
0

4
0

10
0

4
0

3
0

2
0

10
1

4
0

10
10

8
8

10
0

10
0

5
0

2
0

3
0

10
0

5
0

5
0

10
0

3
0

10
0

4
0

5
0

7
0

4
0

4
0

5
0

4
0

10
0

8
0

5
0

2
0

9
0

10
0

7
0

3
0

10
0

10
0

10
0

10
0

3
0

4
4

2
0

2
0

9
0

8
0

10
0

4
0

2
0

10
0

5
0

2
0

3
0

4
0

7
0

10
0

4
0

3
0

10
0

3
0

3
0

4
0

3
0

3
3

10
0

7
0

10
0

3
3

10
0

2
2

5
0

6
6

4
0

3
3

4
4

10
0

5
0

10
10

2
0

6
0

8
0

10
0

9
0

2
0

7
0

9
9

2
0

2
2

10
10

2
0

4
4

4
0

2
2

2
2

9
9

4
0

4
0

9
0

10
0

10
0

2
2

5
0

10
0

10
10

2
0

10
0

10
0

10
0

9
0

2
0

10
0

10
0

4
4

3
0

10
0

6
6

5
0

4
0

10
0

10
10

5
0

5
0

2
0

10
10

5
5

9
0

2
2

5
0

6
0

6
6

10
10

3
0

8
0

4
0

10
0

6
0

4
0

8
8

4
4

8
8

7
7

2
2

2
0

3
0

10
0

4
4

2
0

2
0

2
2

3
0

2
2

4
4

3
0

4
0

3
0

3
3

10
0

10
0

8
8

7
7

10
10

6
0

2
0

4
0

3
3

10
10

3
3

10
0

8
8

10
0

10
10

10
0

7
7

5
0

4
0

10
0

2
2

3
0

2
0

4
4

2
2

10
10

10
10

10
10

6
6

3
0

2
2

10
10

2
2

4
4

10
0

10
10

2
2

1

2
0

10
0

10
0

6
0

2
0

3
3

10
0

5
0

2
0

3
3

10
0

10
10

10
0

4
0

4
0

4
0

6
6

2
0

5
0

10
10

9
0

2
2

9
9

3
3

5
5

7
7

6
6

10
0

2
2

3
0

4
0

2
0

3
0

10
10

2
0

3
3

2
2

10
0

3
3

2
0

6
0

2
0

5
5

6
6

6
0

2
0

3
0

10
10

2
0

9
0

10
0

5
0

2
0

4
0

3
0

10
0

2
0

10
0

10
0

10
0

5
0

8
0

2
0

10
0

4
0

9
0

7
0

3
0

3
0

10
0

4
0

10
10

6
0

4
4

2
0

4
0

10
10

2
2

2
2

10
10

3
3

10
10

2
2

10
10

4
4

2
2

2
2

3
3

3
0

6
0

2
0

7
7

10
10

3
3

10
10

10
0

10
10

4
0

2
2

8
0

7
0

5
0

10
0

9
0

2
0

5
5

10
0

3
0

2
0

9
0

2
2

10
0

4
0

7
0

10
0

3
0

3
0

10
0

3
0

5
0

10
0

4
4

8
8

4
0

2
2

2
2

6
0

6
0

8
0

5
0

7
0

7
0

3
0

10
0

10
10

5
0

2
0

6
0

7
0

8
0

9
0

3
0

10
0

2
0

2
0

9
0

4
0

7
0

5
0

2
0

3
0

10
0

6
0

9
0

3
0

2
0

9
0

5
0

9
0

10
0

8
8

10
0

3
3

9
0

10
0

2
0

2
0

10
0

8
0

5
0

2
0

2
0

5
0

5
0

10
0

8
0

2
0

6
0

10
0

2
2

10
0

9
0

8
0

10
0

5
0

10
0

4
0

2
0

6

0

5
0

2
2

10
0

3
3

10
0

2
2

10
10

10
10

10
0

7
7

9
9

2
0

9
9

2
2

2
0

5
5

4
4

3
0

7
7

10
10

8
8

10
10

2
2

5
5

5
5

8
8

10
10

10
10

10
10

10
10

10
10

4
4

3
0

3
0

2
2

2
2

10
10

2
2

10
10

4
0

2
2

8
8

2
2

3
3

2
2

10
0

8
8

10
10

4
0

3
0

2
2

5
0

2
2

4
4

2
0

5
0

5
5

2
2

2
2

4
0

10
10

2
0

4
4

4
4

10
0

10
10

2
2

2
2

2
2

3
3

7
7

2
2

10
10

10
10

10
10

2
2

4
4

2
2

10
10

5
5

2
2

4
4

2
2

3
3

6
0

2
2

2
0

2
0

10
10

10
0

4
4

3
3

2
2

2
2

9
9

2
2

10
0

10
10

2
2

5
0

10
10

10
10

3
3

3
3

3
3

2
2

9
0

4
0

6
6

5
5

10
0

3
3

7
7

2
0

3
0

10
10

5
5

9
9

10
0

2
2

5
0

3
3

10
0

4
4

8
8

7
7

6
6

2
0

3
3

10
10

4
4

3
3

10
10

2
2

10
0

2
2

2
0

4
0

2
0

2
2

2
2

5
5

4
4

10
10

3
3

2
2

5
5

6
6

3
0

10
0

2
2

2
2

2
2

2
0

4
4

8
8

3
3

2
2

6
0

2
0

3
0

10
0

10
0

5
5

4
4

6
6

3
0

4
4

10
10

2
2

4
4

5
5

3
3

10
0

6
6

2
2

3
3

2
0

10
10

2
2

2
0

2
2

5
0

4
4

2
2

6

1508260704

In [196]:
len(listie)

2779

In [199]:
zee = pd.DataFrame(listie)

In [202]:
EZZ = pd.merge(zee, dupos, left_on=['CUSTOMER_NBR','NPI'], right_on=['CUSTOMER_KEY','NPI'])

In [204]:
hope = pd.concat([solos, EZZ])

C:\Users\vigrose\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:1: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  """Entry point for launching an IPython kernel.


In [206]:
LETSGO = pd.merge(CUSTOMER, hope, left_on='CUSTOMER_NBR', right_on='CUSTOMER_KEY', suffixes = ['','_NBR'])

In [207]:
LETSGO.to_csv('../../Data/Credentialling/Matched_Customers.csv',index=False)

In [295]:
pd.DataFrame(bopp)[['CUSTOMER_KEY', 'NAME', 'OTHER_NAME', 'NPI', 'TAXONOMY', 'SUBPART',
       'MAILING_ADDRESS',  'LOCATION_ADDRESS', 'MAILING_CITY', 'MAILING_STATE',
         'LOCATION_CITY', 'LOCATION_STATE']][134:]

CUSTOMER_KEY  \
134  The Ambulatory Surgery Center At St. Mary   
135                            Bryn Mawr Rehab   
136                         Shriners Hospitals   
137                         Shriners Hospitals   
138                         Shriners Hospitals   
139                         Shriners Hospitals   
140                 New Britain Surgery Center   

                                               NAME  \
134  THE AMBULATORY SURGERY CENTER AT ST. MARY, LLC   
135                       MAIN LINE HOSPITALS, INC.   
136                 SHRINERS HOSPITALS FOR CHILDREN   
137                 SHRINERS HOSPITALS FOR CHILDREN   
138                 SHRINERS HOSPITALS FOR CHILDREN   
139  SHRINERS HOSPITALS FOR CHILDREN - PHILADELPHIA   
140                  NEW BRITAIN SURGERY CENTER LLC   

                                            OTHER_NAME         NPI  \
134                                               None  1154624526   
135                  BRYN MAWR REHABILITATION HOSPITAL  1396850368   
136                                               None  1558404632   
137  SHRINERS HOSPITALS FOR CHILDREN PROFESSIONAL S...  1659615706   
138  SHRINERS HOSPITALS FOR CHILDREN PROFESSIONAL A...  1023506276   
139                                               None  1124395017   
140                                               None  1063715951   

                                              TAXONOMY SUBPART  \
134                  Clinic/Center Ambulatory Surgical      NO   
135                            Rehabilitation Hospital      NO   
136               General Acute Care Hospital Children      NO   
137  Orthopaedic Surgery Pediatric Orthopaedic Surgery      NO   
138            Anesthesiology Pediatric Anesthesiology      NO   
139                                   Special Hospital      NO   
140                  Clinic/Center Ambulatory Surgical      NO   

                                  MAILING_ADDRESS           LOCATION_ADDRESS  \
134                     1203 LANGHORNE NEWTOWN RD  1203 LANGHORNE NEWTOWN RD   
135                   3803 W CHESTER PIKE STE 250             414 PAOLI PIKE   
136                   P.O. BOX 8500 LOCKBOX #7642            3551 N BROAD ST   
137                                   PO BOX 8500            3551 N BROAD ST   
138                     PO BOX 8500 LOCKBOX #7642            3551 N BROAD ST   
139  SHRINERS HOSPITALS FOR CHILDREN PHILADELPHIA            3551 N BROAD ST   
140                          1200 MANOR DR STE 40              1200 MANOR DR   

       MAILING_CITY MAILING_STATE LOCATION_CITY LOCATION_STATE  
134       LANGHORNE            PA     LANGHORNE             PA  
135  NEWTOWN SQUARE            PA       MALVERN             PA  
136    PHILADELPHIA            PA  PHILADELPHIA             PA  
137    PHILADELPHIA            PA  PHILADELPHIA             PA  
138    PHILADELPHIA            PA  PHILADELPHIA             PA  
139    PHILADELPHIA            PA  PHILADELPHIA             PA  
140        CHALFONT            PA      CHALFONT             PA

In [294]:
len(pd.DataFrame(bopp))

141

In [15]:
customers = pd.read_csv("../../Data/Credentialling/Resident_cust.csv")

In [16]:
orgs = customers.rename(columns={'Customer Number': 'Customer_Number','Company Name': 'Company_Name','Zip Code': 'Zipcode'})

In [18]:
len(orgs)

2829

In [21]:
index = 0

In [24]:
new_list =[]

In [29]:
orgs = orgs.fillna('None')

In [30]:
for row in orgs[index:].itertuples():
#     print(int(row.NPI))
    print('')
    zipcode = str(row.Zipcode)[0:5]
    name = row.Company_Name.replace('.','')
    new_results = get_results(Search(name, row.State, row.City, zipcode))
    parsed = parse_results(new_results, row.CUSTOMER_NBR)
    if not parsed:
        print('No results found')
        cus_name = name.replace('+','')+'*'
        new_results = get_results(Search(cus_name, row.State, row.City))
        parsed = parse_results(new_results, row.CUSTOMER_NBR)
        if not parsed:
            print('ahh')
            new_results = get_results(Search("",row.State, row.City, row.Zipcode))
            parsed = parse_results(new_results, row.CUSTOMER_NBR)
    new_list.append(parsed)
    if parsed:
        print(F'{row.Company_Name} matched to {parsed[0]["NAME"]}')
    else:
        print(F'{row.Company_Name} needs help')
    index += 1


No results found
None matched to JOHN B MARTIN MD

Atlanta VAMC matched to ATLANTA VAMC

No results found
ahh
New York GI Center, LLC matched to STEPHANIE ANN SALAS MD PLLC

No results found
Jamaica Medical Center matched to JAMAICA MEDICAL CENTER NY PC

No results found
University Hospital matched to UNIVERSITY HOSPITAL - CAMDEN EMS DIVISION

Reid Hospital & Health Care Services matched to REID HOSPITAL & HEALTH CARE SERVICES

No results found
ahh
The Surgery and Laser Center needs help

CarolinaEast Health System matched to CAROLINAEAST HEALTH SYSTEM

AdventHealth Gordon matched to ADVENTIST HEALTH SYSTEM GEORGIA, INC.

Murray Medical Center matched to MURRAY COUNTY MEMORIAL HOSPITAL AUTHORITY

No results found
CHRISTUS Spohn Health System matched to CHRISTUS SPOHN HEALTH SYSTEM CORPORATION

The Vines Hospital matched to OCALA BEHAVIORAL HEALTH, LLC

No results found
ahh
Arthroscopic & Laser Surgery Center of San Diego, LP matched to WEMMER AND ASSOCIATES MEDICAL GROUP INC

No resul

No results found
Hudson Regional Hospital matched to NJMHMC, LLC

Eastern State Hospital matched to DEPARTMENT OF SOCIAL DEPT OF SHS DIV OF INSTNS

No results found
Baylor Scott & White matched to TEXAS REGIONAL MEDICAL CENTER, LLC

No results found
ahh
McLaren - Greater Lansing matched to MCLAREN GREATER LANSING

Arizona Specialty Hospital matched to ORTHOPEDIC AND SURGICAL SPECIALTY COMPANY, LLC

No results found
Seton Medical Center matched to SETON MEDICAL CENTER AUSTIN

Providence Sacred Heart Medical Center matched to PROVIDENCE SACRED HEART MEDICAL CENTER

No results found
Blackhawk Plastic Surgery matched to BLACKHAWK PLASTIC SURGERY, A MEDICAL CORP.

No results found
ahh
Middle Tennessee Medical Center Inc. matched to MURFREESBORO RADIOLOGY & NUCLEAR MED CONSLT, INC.

Gila River Health Care matched to GILA RIVER HEALTH CARE

Witham Health Services matched to WITHAM HEALTH SERVICES

Perry County Memorial Hospital matched to PERRY COUNTY MEMORIAL HOSPITAL

No results found
ahh
K

Cox Medical Center Branson matched to SKAGGS COMMUNITY HOSPITAL ASSOCIATION

No results found
ahh
Neurotech, LLC and Neurotech Northwest, LLC matched to NEUROTECH, LLC

Navarro Regional Hospital matched to NAVARRO REGIONAL HOSPITAL

University of Maryland Medical Center matched to UNIVERSITY OF MARYLAND MEDICAL CENTER

No results found
ahh
VA Med Ctr needs help

Port Jefferson Asc, LLC matched to PORT JEFFERSON ASC, LLC

No results found
Millinocket Regional Hospital matched to MILLINOCKET REGIONAL HOSPITAL

No results found
ahh
Stormont-Vail Regional Medical Center needs help

Tampa Outpatient Surgical Facility matched to FLORIDA SURGERY CENTER ENTERPRISES LLC

Lakeland Regional Medical Center matched to LAKELAND REGIONAL MEDICAL CENTER, INC.

No results found
ahh
Olympic Memorial Hospital matched to SHERIDAN HEALTHCARE OF WASHINGTON, PC

Guam Regional Medical City matched to GUAM HEALTHCARE DEVELOPMENT INCORPORATED

No results found
Knapp Medical Center matched to KNAPP MEDICAL CENTE

Inspira Health Network matched to INSPIRA HEALTH NETWORK MEDICAL GROUP, P.C.

No results found
ahh
Surgical Specialist of St Lucie, LLC matched to EAST COAST ANESTHESIA ASSOCIATES PA

No results found
ahh
The Memorial Hospital At Craig matched to THE MEMORIAL HOSPITAL

No results found
ahh
University Hospital of Denton matched to NORTH TEXAS PSYCHIATRIC ASSOCIATES PA

No results found
Central New York Psychiatric Center matched to CENTRAL NEW YORK PSYCHIATRIC CENTER FOR FORENSICS

No results found
ahh
Campbell Surgery Center matched to CAMPBELL CLINIC, PC

Mary Lanning Healthcare matched to THE MARY LANNING MEMORIAL HOSPITAL ASSOCIATION

No results found
ahh
None matched to WINN-THIRD PARTY INSURANCE

Cornerstone Hospital of Southeast Arizona matched to CORNERSTONE HOSPITAL OF SOUTHEAST ARIZONA LLC

OrthoSouth Surgery Center-Germantown matched to BAPTIST GERMANTOWN SURGERY CENTER, LLC

No results found
ahh
Memorial Health Care Center matched to KNIGHT DRUGS OWOSSO, INC.

No results fou

No results found
Fifth Avenue Surgery Center matched to FIFTH AVENUE SURGERY CENTER, LLC

No results found
ahh
Hackensack University Medical Center at Pascack Valley needs help

No results found
ahh
University Medical Center-Mesabi matched to THE DULUTH CLINIC, LTD

No results found
Posada Ambulatory Surgery Center matched to POSADA AMBULATORY SURGERY CENTER, LP

Valley Health Team, Inc. matched to VALLEY HEALTH TEAM, INC

No results found
ahh
Altus Emergency Centers matched to ALTUS LUMBERTON, LP

Lake Charles Memorial Hospital matched to SOUTHWEST LOUISIANA HOSPITAL ASSOCIATION

No results found
WEST LA SURGERY CENTER matched to WEST LA SURGERY CENTER, LLC

Adventist HealthCare White Oak Medical Center matched to ADVENTIST HEALTHCARE, INC.

Candler County Hospital matched to HOSPITAL AUTHORITY OF CANDLER COUNTY

No results found
Northeast Hospital Corporation matched to NORTHEAST HOSPITAL CORPORATION

Mary Washington Hospital matched to MARY WASHINGTON HOSPITAL

No results found
ahh


...

Va Loma Linda Healthcare System matched to VA LOMA LINDA HEALTHCARE SYSTEM

No results found
ahh
EL PASO LTAC HOSPITAL matched to EL PASO LTAC PARTNERS LP

University of Maryland Surgery Center matched to UNIVERSITY OF MARYLAND MEDICINE ASC, LLC

No results found
Herndon Surgery Center, Inc. matched to HERNDON SURGERY CENTER, INC.

No results found
Rehabilitation Hospital of Indiana matched to REHABILITATION HOSPITAL OF INDIANA, INC.

Salt Creek Surgery Center matched to WESTMONT SURGERY CENTER LLC

Douglas County Hospital matched to DOUGLAS COUNTY HOSPITAL

No results found
ahh
Rchp Billings - Missoula, Llc, D/B/A Community Medical Center matched to BIG SKY SURGERY CENTER, LLC

Indiana Spine Hospital, LLC matched to INDIANA SPINE HOSPITAL, LLC

No results found
Tri-State Surgery Center matched to TRI-STATE SURGERY CENTER, L.L.C.

No results found
Parkside Surgery Center matched to PARKSIDE SURGERY CENTER, LLC

The Colony Er Hospital matched to HEALTHCARE HL EMERGENCY SERVICES, LLC

No

No results found
ahh
Orthoatlanta Surgery Center Austell matched to BIO-MEDICAL APPLICATIONS OF GEORGIA, INC.

Ohio Hills Health Services matched to OHIO HILLS HEALTH SERVICES

El Paso Behavioral Health System matched to UNIVERSITY BEHAVIORAL HEALTH OF EL PASO, LLC

Blackfeet Community Hospital matched to BLACKFEET COMMUNITY HOSPITAL

No results found
ahh
Houma Outpatient Surgery Center needs help

South Hills Surgery Center, LLC matched to SOUTH HILLS SURGERY CENTER, LLC

No results found
ahh
The Community Health Center of Branch County needs help

No results found
ahh
MidTowne Surgical Center matched to MICHIGAN SLEEP NETWORK, P.C.

No results found
Sequoia Surgery Center matched to SEQUOIA SURGERY CENTER, LLC

No results found
Madison Health matched to MADISON COUNTY COMMUNITY HOSPITAL

No results found
ahh
EMHS needs help

No results found
Progressive Surgical Institute matched to PROGRESSIVE SURGICAL INSTITUTE INC.

No results found
Center for Ambulatory Surgery matched to CENTER 

No results found
ahh
Chicago Lakeshore Hospital (HCA) needs help

Bakersfield Family Medical Center matched to BAKERSFIELD FAMILY MEDICAL GROUP

Oceans Hospital of Broussard matched to OCEANS BEHAVIORAL HOSPITAL OF LAFAYETTE LLC

Valley Forge Medical Center matched to VALLEY FORGE MEDICAL CENTER & HOSPITAL, INC.

No results found
Northern Virginia Eye Surgery Center matched to NORTHERN VIRGINIA EYE SURGERY CENTER, LLC

Three Rivers Behavioral Health matched to THREE RIVERS BEHAVIORAL HEALTH LLC

No results found
ahh
Sarasota Memorial PHO matched to GOOD BUSINESS LLC

Mendota Mental Health Institute matched to MENDOTA MENTAL HEALTH INSTITUTE

No results found
ahh
California Hospital Med Ctr matched to CALIFORNIA HOSPITAL RADIOLOGY MEDICAL GROUP PC

No results found
Bacon County Health Services matched to BACON COUNTY HEALTH SERVICES, INC

No results found
SAME DAY SURGICLINIC matched to SAME DAY SURGICARE OF NEW ENGLAND, INC.

Wallowa County Health Care District matched to WALLOWA COUNT

No results found
ahh
Endoscopy Consultants LLC needs help

Surgery Center of Naples, LLC matched to SURGERY CENTER OF NAPLES, LLC

Center for Day Surgery matched to CENTER FOR DAY SURGERY

Arkansas Center for Surgical Excellence matched to ARKANSAS CENTER FOR SURGICAL EXCELLENCE

No results found
ahh
WCHC - Hamtramck Health Center matched to GLORY PHARMACY- JOSEPH CAMPAU LLC

No results found
ahh
Westside Outpatient Center, LLC DBA Palms Wellington Surgical Center matched to CENTER FOR BONE & JOINT SURGERY OF THE PALM BEACHES, P.A.

No results found
Texarkana Surgery Center matched to TEXARKANA SURGERY CENTER LP

No results found
ahh
Community Methodist Hospital needs help

No results found
ahh
SURGICAL SPECIALISTS, ASC matched to EMERALD COAST EYE INSTITUTE LLC

No results found
ahh
Boise Veterans Affairs Medical Center matched to BOISE VAMC

Illinois Valley Community Hospital matched to ILLINOIS VALLEY COMMUNITY HOSPITAL

Oxford Surgery Center matched to BAPTIST AND PHYSICIANS OUTPAT

No results found
NF/SG VETERANS HEALTH SYSTEM matched to NF/SG VETERANS HEALTH SYSTEM

No results found
ahh
Filutowski Eye Institute, P.A. matched to FILUTOWSKI EYE INSTITUTE PA

Crown Point Surgery Center matched to CROWN POINT SURGERY CENTER, LLC

No results found
SAS Surgery Center matched to SAS SURGERY CENTER, LLC

No results found
ahh
Valley Eye  Surgical Center matched to LASER VISION CENTERS, INC.

No results found
ahh
PCAS matched to RICHARD A. GANGNES M.D. INC.

No results found
ahh
Surgery Center Chevy Chase matched to THE TRAINING ROOM INC

Johnson City Eye Surgery Center matched to JOHNSON CITY EYE SURGERY CENTER

Beatrice Community Hospital & Health Center matched to BEATRICE COMMUNITY HOSPITAL & HEALTH CENTER

No results found
ahh
Surgcenter of St. Lucie, LLC matched to BEE WELL PEDIATRICS

No results found
Piney Orchard Surgery Center matched to PINEY ORCHARD SURGERY CENTER, LLC.


In [31]:
len(new_list)

2829

In [35]:
listy=[]
for thing in new_list:
    listy+=thing

In [41]:
XYZ = pd.merge(pd.DataFrame(listy), orgs, left_on='CUSTOMER_KEY', right_on='CUSTOMER_NBR')

In [65]:
XYZ[['MAILING_ADDRESS', 'LOCATION_ADDRESS','Street 1ST', 'Zipcode','LOCATION_ZIP']][0:10]

MAILING_ADDRESS   LOCATION_ADDRESS              Street 1ST  \
0        2425 GEARY BLVD    2425 GEARY BLVD  2350 Geary Blvd 3rd Fl   
1  12254 BELLFLOWER BLVD    4131 GEARY BLVD  2350 Geary Blvd 3rd Fl   
2        2425 GEARY BLVD    2425 GEARY BLVD  2350 Geary Blvd 3rd Fl   
3        2425 GEARY BLVD    2425 GEARY BLVD  2350 Geary Blvd 3rd Fl   
4        4131 GEARY BLVD    4131 GEARY BLVD  2350 Geary Blvd 3rd Fl   
5        4131 GEARY BLVD    4131 GEARY BLVD  2350 Geary Blvd 3rd Fl   
6        4131 GEARY BLVD    4131 GEARY BLVD  2350 Geary Blvd 3rd Fl   
7          PO BOX 330283    910 MARSHALL ST  2350 Geary Blvd 3rd Fl   
8   350 N HUMPHREYS BLVD  2301 S LAMAR BLVD    350 N Humphreys Blvd   
9   350 N HUMPHREYS BLVD   255 BAPTIST BLVD    350 N Humphreys Blvd   

     Zipcode LOCATION_ZIP  
0  941153305    941153358  
1  941153305    941183101  
2  941153305    941153358  
3  941153305    941153358  
4  941153305    941183101  
5  941153305    941183101  
6  941153305    941183101  
7  941153305    940632033  
8  381202177    386555373  
9  381202177    397052011

In [58]:
def check_match(thing_1, thing_2):
    '''match check'''
    if thing_1 == thing_2:
        return 1
    elif thing_1 in thing_2 or thing_2 in thing_1:
        return 1
    elif fuzz.ratio(thing_1, thing_2) > 70:
        return 1
    else:
        return 0

In [67]:
Z='VICTO'
Z[0:4]

'VICT'

In [68]:
dict_list = []
for row in XYZ.itertuples():
    zip_match = 0
    if check_match(row.NAME,row.CUSTOMER_NAME.upper()) == 1:
        name_match = 1
    else:
        name_match = check_match(row.OTHER_NAME, row.CUSTOMER_NAME.upper())
    if check_match(row.LOCATION_ADDRESS, row.street_1.upper()) == 1:
        add_match = 1
    else:
        add_match = check_match(row.MAILING_ADDRESS, row.street_1.upper())
    if row.Zipcode == row.LOCATION_ZIP or str(row.Zipcode)[0:5] == str(row.LOCATION_ZIP)[0:5]:
        zip_match = 1
    new_dict = {
        'NPI':row.NPI,
        'CUSTOMER_NBR': row.CUSTOMER_NBR,
        'NAME_MATCH': name_match,
        'ADD_MATCH': add_match,
        'ZIP_MATCH': zip_match
    }
    dict_list.append(new_dict)

In [70]:
matches = pd.DataFrame(dict_list)

In [72]:
tutu = pd.merge(XYZ, matches, on=['CUSTOMER_NBR','NPI'])

In [79]:
YES = tutu[(tutu.NAME_MATCH==1)&(tutu.ZIP_MATCH==1)|(tutu.NAME_MATCH==1)&(tutu.ADD_MATCH==1)]

In [82]:
yess = YES.drop_duplicates('CUSTOMER_NBR', keep=False)

In [88]:
duplicado = YES[YES.CUSTOMER_NBR.isin(yess.CUSTOMER_NBR)==False]

In [101]:
doubles = duplicado.drop_duplicates('CUSTOMER_NBR')['CUSTOMER_NBR']

In [100]:
doubles

2100814

In [115]:
NEW_LIST =[]
df = pd.DataFrame()
for double in doubles:
    print('')
    print(double)
    new_df = duplicado[duplicado.CUSTOMER_NBR == double]
    print(len(new_df))
    new_df_2 = new_df[new_df.TAXONOMY == 'General Acute Care Hospital']
    if len(new_df_2)== 0:
        new_df_2 = new_df[(new_df.ADD_MATCH == 1)& (new_df.ZIP_MATCH==1)]
        if len(new_df_2)== 0:
            new_df_2 = new_df[new_df.SUBPART == 'NO']
            if len(new_df_2)==0:
                print('wtf')
                continue
    if len(new_df_2) >1:
        new_df_2 = new_df_2[(new_df_2.ADD_MATCH == 1)& (new_df_2.ZIP_MATCH==1)]
        if len(new_df_2)> 1:
                new_df_2 = new_df_2[new_df_2.SUBPART == 'NO']
                if len(new_df_2)>1:
                    print('wtf 2')
                    print(len(new_df_2))
                    df = pd.concat([df, new_df_2])
    if len(new_df_2) == 1:
        print('MATCH!')
        npi = new_df_2.iloc[0]['NPI']
        NEW_DICT = {
            'NPI': npi,
            'CUSTOMER_NBR': double
        }
        NEW_LIST.append(NEW_DICT)


2100814
3
MATCH!

2080785
3
wtf 2
3

2080849
10
wtf 2
4

2080732
2
wtf 2
2

3422273
2
wtf 2
2

2612632
2

2083355
10

2084912
5
wtf 2
5

2083652
2
MATCH!

2083118
9
wtf 2
2

2083169
2
MATCH!

2085085
6
wtf 2
3

2041391
2
wtf 2
2

2083838
2

2083880
2
MATCH!

2103615
7
MATCH!

2188826
3
MATCH!

2188811
8
wtf 2
3

2082964
5
MATCH!

2085467
4

2085170
2

2080776
6
MATCH!

2086408
3

2080118
3

2080805
2

2040899
10
wtf 2
2

1921001
2

2149054
2
MATCH!

2080204
2
MATCH!

2080380
10
MATCH!

2105949
5
MATCH!

2083407
5
wtf 2
3

2084259
4
wtf 2
2

2080996
3
MATCH!

2083469
4

487015
5
MATCH!

2083411
4
wtf 2
2

2084525
9
wtf 2
7

2080127
3
MATCH!

2083522
2
MATCH!

2320759
2
wtf 2
2

2084301
10

2083158
4
MATCH!

2080140
7

2080308
3
wtf 2
2

2083425
6
wtf 2
2

2086092
10
MATCH!

2084251
10
wtf 2
7

2083635
2
MATCH!

1662198
5
wtf 2
2

2080319
10

2080792
5

2080139
3
MATCH!

2086143
2
MATCH!

2350323
3
wtf 2
2

2084508
2
MATCH!

2083674
7
wtf 2
2

2081012
2
MATCH!

2081838
10
wtf 2
4

20808


2084544
2
MATCH!

2087308
3
wtf 2
2

2083894
2
MATCH!

2083746
10
MATCH!

2080131
7
wtf 2
4

2083663
2

2082986
3
MATCH!

2084011
2

2080195
3
MATCH!

2083133
3
MATCH!

2051067
5

2188798
2
MATCH!

2102642
5
MATCH!

2083476
2
MATCH!

2086186
5
wtf 2
5

2084246
6

2082942
10
MATCH!

2105023
9

2081063
2
MATCH!

2080089
5
wtf 2
2

2086178
6
wtf 2
3

2084252
9

2080903
6
MATCH!

2085063
6
wtf 2
6

3082248
3
MATCH!

2083783
9
MATCH!

2088111
2
wtf 2
2

2614296
9
wtf 2
4

2085590
10
MATCH!

2082958
3
wtf 2
2

2080738
6
MATCH!

2084528
9
wtf 2
2

2084591
8
MATCH!

2188821
2
MATCH!

2100984
2
MATCH!

2085136
5
wtf 2
4

2084526
4
wtf 2
3

2102086
6
wtf 2
2

2086473
5
MATCH!

2084895
10
MATCH!

2084590
2

2086434
4
wtf 2
3

2080189
3
MATCH!

2085053
3
wtf 2
2

2083845
2
wtf 2
2

2083234
9
MATCH!

2085935
10
wtf 2
2

2084297
3
MATCH!

2080137
4
wtf 2
2

2083117
9
wtf 2
6

2082993
3
MATCH!

2083796
10
wtf 2
5

2084520
10
MATCH!

2084808
9
MATCH!

2084839
10
wtf 2
3

2188886
6

2087870
3
MATCH!




2099150
2
MATCH!

2086799
10
wtf 2
4

2085144
6
wtf 2
4

2083474
5
wtf 2
5

2100531
3
wtf 2
2

2084033
9
wtf 2
5

2084002
2

2084013
3
MATCH!

2083994
2
MATCH!

2074675
2
wtf 2
2

2369653
4
MATCH!

2087038
4
wtf 2
3

2081417
3
wtf 2
2

2083267
10

2083311
5
MATCH!

2085519
7
wtf 2
2

2088164
3
wtf 2
2

2087642
5
wtf 2
5

2088081
10
wtf 2
8

2085547
10
MATCH!

2085760
5
MATCH!

2100891
2
wtf 2
2

2087478
5
MATCH!

2085017
2
MATCH!

2403001
10
wtf 2
10

3159973
10
wtf 2
8

2085143
4
wtf 2
2

2084704
2
MATCH!

2099939
2
MATCH!

2087795
2

2085680
7
MATCH!

3199328
2
MATCH!

2103594
2
wtf 2
2

1628000
4
MATCH!

2101391
3
MATCH!

2109081
10

2083877
2
MATCH!

2087116
4
wtf 2
4

2088532
3
wtf 2
3

2086288
2
wtf 2
2

2088278
9
MATCH!

2079923
4
wtf 2
2

2103104
3
wtf 2
3

2099972
2
wtf 2
2

2085197
5
MATCH!

2099153
2
MATCH!

2087628
5
MATCH!

2087040
8
wtf 2
2

2086012
2
MATCH!

2085525
3
MATCH!

2085297
6
wtf 2
4

2108663
3
MATCH!

2087924
5
wtf 2
5

2086136
3
wtf 2
2

2087760
3

2083468
5

In [106]:
len(NEW_LIST)

540

In [107]:
len(doubles)

1290

In [110]:
duplicado[['NAME', 'OTHER_NAME', 'NPI', 'TAXONOMY', 'SUBPART',
       'MAILING_ADDRESS', 'MAILING_ZIP', 
       'LOCATION_ADDRESS', 'LOCATION_ZIP', 
       'UPDATED', 'CUSTOMER_NAME',
       'CUSTOMER_NBR', 'Zipcode', 'street_1', 'NAME_MATCH',
       'ADD_MATCH', 'ZIP_MATCH']]

NAME  \
0                  KAISER FOUNDATION HOSPITALS   
2                  KAISER FOUNDATION HOSPITALS   
3                  KAISER FOUNDATION HOSPITALS   
18             FRANKLIN SQUARE HOSPITAL CENTER   
19             FRANKLIN SQUARE HOSPITAL CENTER   
...                                        ...   
11183                          LHCG XXIII, LLC   
11184        MARSHALL COUNTY HOSPITAL DISTRICT   
11185  MARSHALL COUNTY HOSPITAL LONG TERM CARE   
11186           PHYSICIANS MEDICAL CENTER, LLC   
11191           PHYSICIANS MEDICAL CENTER, LLC   

                                              OTHER_NAME         NPI  \
0               KAISER FOUNDATION HOSPITAL SAN FRANCISCO  1134299522   
2                 KAISER FDN HSP INP/OUT HSP PHY 31A 315  1023160009   
3          KAISER FOUNDATION HOSPITAL SAN FRANCISCO ESRD  1710052428   
18                                                  None  1518141019   
19                                                  None  1023319282   
...                                                  ...         ...   
11183               MARSHALL COUNTY HOSPITAL HOME HEALTH  1376845834   
11184           MARSHALL COUNTY SURGICAL & MEDICAL GROUP  1962873109   
11185                                               None  1336205897   
11186  TEXAS HEALTH CENTER FOR DIAGNOSTICS AND SURGER...  1316933609   
11191  TEXAS HEALTH CENTER FOR DIAGNOSTICS AND SURGER...  1982809257   

                                                TAXONOMY SUBPART  \
0                            General Acute Care Hospital      NO   
2                     Pharmacy Community/Retail Pharmacy      NO   
3      Clinic/Center End-Stage Renal Disease (ESRD) T...      NO   
18                           General Acute Care Hospital      NO   
19                           General Acute Care Hospital      NO   
...                                                  ...     ...   
11183                         Clinic/Center Rural Health      NO   
11184                         Clinic/Center Rural Health      NO   
11185        Nursing Facility/Intermediate Care Facility      NO   
11186                        General Acute Care Hospital      NO   
11191                        General Acute Care Hospital      NO   

               MAILING_ADDRESS MAILING_ZIP         LOCATION_ADDRESS  \
0              2425 GEARY BLVD   941153358          2425 GEARY BLVD   
2              2425 GEARY BLVD   941153358          2425 GEARY BLVD   
3              2425 GEARY BLVD   941153358          2425 GEARY BLVD   
18     9000 FRANKLIN SQUARE DR   212373901  9000 FRANKLIN SQUARE DR   
19      22812 POINT LOOKOUT RD   206506104  9000 FRANKLIN SQUARE DR   
...                        ...         ...                      ...   
11183             PO BOX 51266   705051266    501 GEORGE MCCLAIN DR   
11184      619 OLD SYMSONIA RD   420255094      619 OLD SYMSONIA RD   
11185    503 GEORGE MCCLAIN DR   420251331    503 GEORGE MCCLAIN DR   
11186            PO BOX 676266   752676266         6020 W PARKER RD   
11191            PO BOX 676266   752676266         6020 W PARKER RD   

      LOCATION_ZIP     UPDATED                              CUSTOMER_NAME  \
0        941153358  2015-08-18                 Kaiser Foundation Hospital   
2        941153358  2010-11-24                 Kaiser Foundation Hospital   
3        941153358  2015-08-18                 Kaiser Foundation Hospital   
18       212373901  2007-12-20            Franklin Square Hospital Center   
19       212373901  2010-11-04            Franklin Square Hospital Center   
...            ...         ...                                        ...   
11183    420251365  2016-05-25                   Marshall County Hospital   
11184    420255094  2015-10-14                   Marshall County Hospital   
11185    420251331  2020-08-22                   Marshall County Hospital   
11186    750938171  2014-02-07  Texas Health Center Diagnostics & Surgery   
11191    750938171  2014-02-07  Texas Health Center Diagnos

In [116]:
df

CUSTOMER_KEY                               NAME  \
18          2080785    FRANKLIN SQUARE HOSPITAL CENTER   
19          2080785    FRANKLIN SQUARE HOSPITAL CENTER   
20          2080785    FRANKLIN SQUARE HOSPITAL CENTER   
23          2080849          INTERFAITH MEDICAL CENTER   
26          2080849          INTERFAITH MEDICAL CENTER   
...             ...                                ...   
11180       2087088  MARSHALL COUNTY HOSPITAL DISTRICT   
11181       2087088  MARSHALL COUNTY HOSPITAL DISTRICT   
11184       2087088  MARSHALL COUNTY HOSPITAL DISTRICT   
11186       2081064     PHYSICIANS MEDICAL CENTER, LLC   
11191       2081064     PHYSICIANS MEDICAL CENTER, LLC   

                                              OTHER_NAME         NPI  \
18                                                  None  1518141019   
19                                                  None  1023319282   
20                                                  None  1932117496   
23                                                  None  1487724712   
26                                                  None  1093047821   
...                                                  ...         ...   
11180                                               None  1790840056   
11181                                               None  1568528594   
11184           MARSHALL COUNTY SURGICAL & MEDICAL GROUP  1962873109   
11186  TEXAS HEALTH CENTER FOR DIAGNOSTICS AND SURGER...  1316933609   
11191  TEXAS HEALTH CENTER FOR DIAGNOSTICS AND SURGER...  1982809257   

                                          TAXONOMY SUBPART  \
18                     General Acute Care Hospital      NO   
19                     General Acute Care Hospital      NO   
20                     General Acute Care Hospital      NO   
23                     General Acute Care Hospital      NO   
26                     General Acute Care Hospital      NO   
...                                            ...     ...   
11180              Medicare Defined Swing Bed Unit      NO   
11181  General Acute Care Hospital Critical Access      NO   
11184                   Clinic/Center Rural Health      NO   
11186                  General Acute Care Hospital      NO   
11191                  General Acute Care Hospital      NO   

                MAILING_ADDRESS MAILING_ZIP MAILING_CITY MAILING_STATE  ...  \
18      9000 FRANKLIN SQUARE DR   212373901    BALTIMORE            MD  ...   
19       22812 POINT LOOKOUT RD   206506104  LEONARDTOWN            MD  ...   
20     2301 FRANKLINS CHANCE CT   210471322     FALLSTON            MD  ...   
23         1545 ATLANTIC AVENUE       11213     BROOKLYN            NY  ...   
26            1545 ATLANTIC AVE   112131122     BROOKLYN            NY  ...   
...                         ...         ...          ...           ...  ...   
11180       615 OLD SYMSONIA RD   420255042       BENTON            KY  ...   
11181       615 OLD SYMSONIA RD   420255042       BENTON            KY  ...   
11184       619 OLD SYMSONIA RD   420255094       BENTON            KY  ...   
11186             PO BOX 676266   752676266       DALLAS            TX  ...   
11191             PO BOX 676266   752676266       DALLAS            TX  ...   

                    Street 1ST Street 2ND Street 3RD       City State  \
18     9000 Franklin Square Dr       None       None  Baltimore    MD   
19     9000 Franklin Square Dr       None       None  Baltimore    MD   
20     9000 Franklin Square Dr       None       None  Baltimore    MD   
23           1545 Atlantic Ave       None       None   Brooklyn    NY   
26           1545 Atlantic Ave       None       None   Brooklyn    NY   
...                        ...        ...        ...        ...   ...   
11180      615 Old Symsonia Rd       None       None     Benton    KY   
11181      615 Old Symsonia Rd       None       None     Benton    KY   
11184      615 Old Symsonia Rd       None       None     Benton    KY   
11186         6020 W 

In [123]:
df_1 = df.sort_values('UPDATED').drop_duplicates('CUSTOMER_NBR', keep='last')

In [129]:
pd.DataFrame(NEW_LIST)['NPI']

0      1134299522
1      1518924109
2      1568435477
3      1174711022
4      1770512626
          ...    
535    1447299953
536    1932547700
537    1184987505
538    1942248737
539    1598901878
Name: NPI, Length: 540, dtype: int64

In [127]:
yess['NPI']

21       1477709244
35       1801202817
38       1932584802
44       1780615492
71       1518090836
            ...    
11205    1437104718
11213    1720012701
11214    1356522726
11216    1053764779
11219    1780618801
Name: NPI, Length: 817, dtype: int64

In [139]:
NEEPS= list(df_1['NPI']) + list(yess['NPI']) + list(pd.DataFrame(NEW_LIST)['NPI'])

In [131]:
matches

NPI  CUSTOMER_NBR  NAME_MATCH  ADD_MATCH  ZIP_MATCH
0      1134299522       2100814           1          0          1
1      1730237561       2100814           1          0          0
2      1023160009       2100814           1          0          1
3      1710052428       2100814           1          0          1
4      1801961511       2100814           1          0          0
...           ...           ...         ...        ...        ...
11215  1023489630       2686870           0          1          1
11216  1053764779       2686870           1          1          1
11217  1205377595       2686870           0          1          1
11218  1235604307       2686870           0          1          1
11219  1780618801       2102226           1          1          1

[11220 rows x 5 columns]

In [143]:
tutu[tutu.NPI.isin(NEEPS)][['CUSTOMER_KEY', 'NAME', 'OTHER_NAME', 'NPI', 'TAXONOMY',
       'LOCATION_ADDRESS', 'LOCATION_ZIP', 'LOCATION_CITY', 'LOCATION_STATE',
       'CUSTOMER_CATEGORY_DESC', 'CUSTOMER_NAME',
       'CUSTOMER_NBR']].to_csv('../../Data/Credentialling/Resident_places.csv', index=False)

In [138]:
orgs

FULL_DT           ME CUSTOMER_CATEGORY_DESC  \
0     2019-07-30   1002131893               Hospital   
1     2019-03-08   2701131676               Hospital   
2     2019-03-08  55004100041               Hospital   
3     2019-04-17  70409060160               Hospital   
4     2019-07-03  64914120711               Hospital   
...          ...          ...                    ...   
2824  2020-08-17   1003150301        Ambulatory Care   
2825  2020-06-23   4814151013        Ambulatory Care   
2826  2020-08-04   3005151154               Hospital   
2827  2020-10-07   1103140061        Ambulatory Care   
2828  2020-07-29   1001141003        Ambulatory Care   

                                        CUSTOMER_NAME  CUSTOMER_NBR  \
0                          Kaiser Foundation Hospital       2100814   
1            Baptist Memorial Health Care Corporation       2080063   
2     St. Joseph Health North California Regional Llc       2100216   
3                     Franklin Square Hospital Center       2080785   
4                        Boca Raton Regional Hospital       2085978   
...                                               ...           ...   
2824                       Surgery Center Chevy Chase       3869263   
2825                  Johnson City Eye Surgery Center       2101048   
2826      Beatrice Community Hospital & Health Center       2084600   
2827                     Surgcenter Of St. Lucie, Llc       2686870   
2828                     Piney Orchard Surgery Center       2102226   

                                         Company_Name  \
0                          Kaiser Foundation Hospital   
1            Baptist Memorial Health Care Corporation   
2     St. Joseph Health North California Regional LLC   
3                     Franklin Square Hospital Center   
4                        Boca Raton Regional Hospital   
...                                               ...   
2824                       Surgery Center Chevy Chase   
2825                  Johnson City Eye Surgery Center   
2826      Beatrice Community Hospital & Health Center   
2827                     Surgcenter of St. Lucie, LLC   
2828                     Piney Orchard Surgery Center   

                              Street 1ST Street 2ND Street 3RD           City  \
0                 2350 Geary Blvd 3rd Fl       None       None  San Francisco   
1                   350 N Humphreys Blvd       None       None        Memphis   
2                     1165 Montgomery Dr       None       None     Santa Rosa   
3                9000 Franklin Square Dr       None       None      Baltimore   
4                         800 Meadows Rd       None       None     Boca Raton   
...                                  ...        ...        ...            ...   
2824         5530 Wisconsin Ave Ste 1620       None       None    Chevy Chase   
2825             110 Med Tech Pkwy Ste 2       None       None   Johnson City   
2826                  4800 Hospital Pkwy       None       None       Beatrice   
2827  10521 SW Village Center Dr Ste 104       None       None  Port St Lucie   
2828           1132 Annapolis Rd Ste 103       None       None        Odenton   

     State    Zipcode  
0       CA  941153305  
1       TN  381202177  
2       CA  954054897  
3       MD  212373997  
4       FL  334862368  
...    ...        ...  
2824    MD  208154322  
2825    TN  376044004  
2826    NE  683106906  
2827    FL  349871930  
2828    MD  211131672  

[2829 rows x 12 columns]